Import necessary libraries and set pandas standards

In [1]:
import os
import geopandas as gp
import pandas as pd
import numpy as np
max_rows = 999
max_cols = 999
pd.set_option("display.max_rows", max_rows, "display.max_columns", max_cols) 

### Import the data

In [2]:
#Set working directory and necessary file paths
wd = os.path.join(os.getcwd(),'NC_2020')
source_files = os.path.join(wd,'raw-from-source')

#VEST shapefile
vest = gp.read_file(os.path.join(os.path.join(source_files,'nc_vest_20'),'nc_vest_20.shp'))
#Unsorted results
unsorted = pd.read_csv(os.path.join(os.path.join(source_files,'results_pct_20201103'),'results_pct_20201103.txt'), delimiter = '\t')
#Sorted results (used for certain counties)
pct_sorted = os.path.join(source_files,'pct_sorted')

In [3]:
#Read in the county-specific filed into a sorted data dictionary with the keys as the county name and value as the dataframe
dfs = []
names = []

for i in os.listdir(pct_sorted):
    path = os.path.join(pct_sorted,i)
    co_df= pd.read_csv(path,delimiter = '\t')
    dfs.append(co_df)
    co_name = str(i.replace('_PRECINCT_SORT.txt',''))
    co_name = str(co_name.replace('_',' '))
    names.append(co_name)
sorted_dict = dict(zip(names,dfs))

## Clean the data

### Drop sorted counties from unsorted and concatenate all back together

In [4]:
unsorted_drop = unsorted[~unsorted['County'].isin(names)]
unsorted_drop.head()

County Election Date Precinct  Contest Group ID Contest Type  \
2        FORSYTH    11/03/2020      081              1342            S   
5   TRANSYLVANIA    11/03/2020       PF              1009            S   
9         CRAVEN    11/03/2020       03              1293            S   
11       SAMPSON    11/03/2020     PLVW              1012            S   
13       FORSYTH    11/03/2020      206                 6            C   

                                         Contest Name  \
2             NC SUPERINTENDENT OF PUBLIC INSTRUCTION   
5                            NC COMMISSIONER OF LABOR   
9                         NC STATE SENATE DISTRICT 02   
11                  NC COURT OF APPEALS JUDGE SEAT 06   
13  CITY OF WINSTON-SALEM COUNCIL MEMBER NORTHEAST...   

                      Choice Choice Party  Vote For  Election Day  One Stop  \
2                Jen Mangrum          DEM         1           204      1076   
5             Jessica Holmes          DEM         1            28       225   
9             Libbie Griffin          DEM         1            60       494   
11              Chris Dillon          REP         1           239      1396   
13  Write-In (Miscellaneous)          NaN         1             0         5   

    Absentee by Mail  Provisional  Total Votes Real Precinct  Unnamed: 15  
2                367            7         1654             Y          NaN  
5                102            0          355             Y          NaN  
9                266            2          822             Y          NaN  
11                70            2         1707             Y          NaN  
13                 8            0           13             Y          NaN

In [5]:
count = 0
for k,v in sorted_dict.items():
    if count == 0:
        sorted_concat = v
        count = 1
    else:
        sorted_concat = pd.concat([sorted_concat,v])
sorted_concat.head()

county_id     county election_dt result_type_lbl result_type_desc  \
0          3  ALLEGHANY  11/03/2020             STD         <NORMAL>   
1          3  ALLEGHANY  11/03/2020             STD         <NORMAL>   
2          3  ALLEGHANY  11/03/2020             STD         <NORMAL>   
3          3  ALLEGHANY  11/03/2020             STD         <NORMAL>   
4          3  ALLEGHANY  11/03/2020             STD         <NORMAL>   

   contest_id                            contest_title  contest_party_lbl  \
0         622  ALLEGHANY COUNTY BOARD OF COMMISSIONERS                NaN   
1         622  ALLEGHANY COUNTY BOARD OF COMMISSIONERS                NaN   
2         622  ALLEGHANY COUNTY BOARD OF COMMISSIONERS                NaN   
3         622  ALLEGHANY COUNTY BOARD OF COMMISSIONERS                NaN   
4         622  ALLEGHANY COUNTY BOARD OF COMMISSIONERS                NaN   

   contest_vote_for precinct_code  \
0                 2            01   
1                 2            01   
2                 2            01   
3                 2            01   
4                 2            01   

                                       precinct_name  candidate_id  \
0  CHERRY LANE                                   ...          1371   
1  CHERRY LANE                                   ...          1371   
2  CHERRY LANE                                   ...          1371   
3  CHERRY LANE                                   ...          1371   
4  CHERRY LANE                                   ...          1371   

       candidate_name candidate_party_lbl  group_num        group_name  \
0  F.O. (Dale) Caveny                 UNA          1      ELECTION DAY   
1  F.O. (Dale) Caveny                 UNA          2          ONE STOP   
2  F.O. (Dale) Caveny                 UNA          3  ABSENTEE BY MAIL   
3  F.O. (Dale) Caveny                 UNA          4       PROVISIONAL   
4  F.O. (Dale) Caveny                 UNA          5          TRANSFER   

  voting_method_lbl voting_method_rslt_desc  vote_ct  
0                 V            Election Day       14  
1                 O      Absentee: One-Stop       49  
2                 M       Absentee: By-Mail       23  
3                 P             Provisional        1  
4                 T  Election Day: Transfer        0

In [6]:
# Reset the sorted data columns
sorted_concat.columns = ["county_id","County","Election Date","result_type_lbl","result_type_desc","contest_id","Contest Name","Choice Party","contest_vote_for","Precinct","Precinct Name","candidate_id","Choice","Choice Party","group_num","group_name","voting_method","voting method_rslt","Total Votes"]

In [7]:
#Sum votes 
sorted_concat_mod = sorted_concat.groupby(['County', 'Contest Name', 'Precinct', 'Choice'])["Total Votes"].sum().reset_index()

In [8]:
#combine
election_results = pd.concat([unsorted_drop,sorted_concat_mod], axis=0, ignore_index=True)

In [9]:
#election_results = unsorted

### Subset by contests of interest

In [10]:
contest_list = sorted(election_results['Contest Name'].unique())
keep_contests = []
for i in contest_list:
    if 'HOUSE OF' in i:
        keep_contests.append(i)
    elif i.startswith('NC STATE SENATE'):
        keep_contests.append(i)
    else:
        continue

In [11]:
#Subset, remove over/under counts and clean Write-In candidates
election_sub = election_results[election_results['Contest Name'].isin(keep_contests)]
election_sub = election_sub[~election_sub['Choice'].isin(['OVER VOTE','UNDER VOTE'])]
election_sub['Choice'] = election_sub['Choice'].apply(lambda x: 'Write-In' if 'Write' in x else x)

### Create party field

In [12]:
election_sub['PARTY'] = election_sub['Choice Party'].apply(lambda x: str(x)[0])
print(election_sub['PARTY'].value_counts())

n    17188
R     3409
D     3372
L      284
C      148
G      139
Name: PARTY, dtype: int64


In [13]:
#Retrieve original party data from the unsorted and input it into the new dataframe
cand_party_dict = dict(zip(list(election_sub['Choice']),list(election_sub['PARTY'])))
for k,v in cand_party_dict.items():
    if v == 'n': #if the value is null
        df = unsorted[unsorted['Choice']==k]
        party_list = df['Choice Party'].unique()
        if len(party_list) == 1: #only one unique party
            party = party_list[0]
            if party.startswith('U'): #this is the Independent designation in NC, for this project they will be considered the equivalent of write-ins
                party = 'O' #write in designation
            election_sub['PARTY'] = election_sub.apply(lambda x: party if x['Choice'] == k else x['PARTY'],axis=1)
            if str(party) == 'n':
                print('There is no party still for: ', k)
        elif len(party_list) == 0:
            party = 'O'
            election_sub['PARTY'] = election_sub.apply(lambda x: party if x['Choice'] == k else x['PARTY'],axis=1)
        else:
            print('For ', k, ' there are multiple parties. They are: ', party_list)
election_sub['PARTY'] = election_sub['PARTY'].apply(lambda x: str(x)[0] if x !='OWRI' else x)

print(election_sub['PARTY'].value_counts())

D    10707
R    10305
L     2406
O      461
G      390
C      271
Name: PARTY, dtype: int64


### Assign legislative level field

In [14]:
election_sub['LEVEL'] = election_sub['Contest Name'].apply(lambda x: (x.split(' ')[0:4]))
election_sub['LEVEL'] = election_sub['LEVEL'].apply(lambda x: ['CON',''] if x[0]=='US' else x)
election_sub['LEVEL'] = election_sub['LEVEL'].apply(lambda x: ['SU',''] if x[1] == 'STATE' else x)
election_sub['LEVEL'] = election_sub['LEVEL'].apply(lambda x: 'SL' if len(x)>2 else x[0])
election_sub.head()

County Election Date Precinct  Contest Group ID Contest Type  \
2      CRAVEN    11/03/2020       03            1293.0            S   
5     FORSYTH    11/03/2020      501            1322.0            S   
35  GRANVILLE    11/03/2020     SOOX            1201.0            S   
36     GASTON    11/03/2020       10            1278.0            S   
38   MCDOWELL    11/03/2020    MAR 3            1413.0            S   

                                Contest Name          Choice Choice Party  \
2                NC STATE SENATE DISTRICT 02  Libbie Griffin          DEM   
5                NC STATE SENATE DISTRICT 31   Joyce Krawiec          REP   
35  NC HOUSE OF REPRESENTATIVES DISTRICT 032   David Woodson          REP   
36  NC HOUSE OF REPRESENTATIVES DISTRICT 109     Susan Maxon          DEM   
38   US HOUSE OF REPRESENTATIVES DISTRICT 11  Tracey DeBruhl          LIB   

    Vote For  Election Day  One Stop  Absentee by Mail  Provisional  \
2        1.0          60.0     494.0             266.0          2.0   
5        1.0          27.0      93.0              18.0          2.0   
35       1.0          47.0     161.0              33.0          1.0   
36       1.0         109.0     630.0             230.0          2.0   
38       1.0           5.0       8.0               2.0          0.0   

    Total Votes Real Precinct  Unnamed: 15 PARTY LEVEL  
2           822             Y          NaN     D    SU  
5           140             Y          NaN     R    SU  
35          242             Y          NaN     R    SL  
36          971             Y          NaN     D    SL  
38           15             Y          NaN     L   CON

### Create last name field with first three letters

In [15]:
election_sub['LASTNAME'] = election_sub['Choice'].apply(lambda x: x.split(' ')[-1])
election_sub['LASTNAME'] = election_sub.apply(lambda x: x['Choice'].split(' ')[-2] if x['LASTNAME'] in ['II','III','Jr.'] else x['LASTNAME'],axis=1)
election_sub['LASTNAME'] = election_sub['LASTNAME'].apply(lambda x: x.replace(',',''))
election_sub['LASTNAME'] = election_sub['LASTNAME'].apply(lambda x: x.rstrip())
election_sub['RESTNAME'] = election_sub.apply(lambda x: x['Choice'].replace(x['LASTNAME'],''),axis=1)
election_sub['RESTNAME'] = election_sub['RESTNAME'].apply(lambda x: x.replace(' , ',' '))
election_sub['WHOLENAME'] = election_sub.apply(lambda x: ', '.join([x['LASTNAME'],x['RESTNAME']]),axis=1)
party_dict = {'D':'(DEM)','R':'(REP)','L':'(LIB)','O':'','G':'(GRE)','C':'(CON)'}
election_sub['PARTY3'] = election_sub['PARTY'].apply(lambda x: party_dict.get(x))
election_sub['CONTEST'] = election_sub['Contest Name'].apply(lambda x: x.upper())
election_sub['NAME_PARTY'] = election_sub.apply(lambda x: ' '.join([x['WHOLENAME'],x['PARTY3']]),axis=1)
election_sub['FIELDS_VAL'] = election_sub.apply(lambda x: ', '.join([x['NAME_PARTY'],x['CONTEST']]),axis=1)

In [16]:
election_sub['LNAME'] = election_sub['Choice'].apply(lambda x: x.split(' ')[-1])
#remove II, III, Jr.
election_sub['LNAME'] = election_sub.apply(lambda x: x['Choice'].split(' ')[-2] if x['LNAME'] in ['II','III','Jr.'] else x['LNAME'],axis=1)
#capitalize
election_sub['LNAME'] = election_sub['LNAME'].apply(lambda x: str(x[:3]).upper())
#set last name as WRI for write in candidates
election_sub['LNAME'] = election_sub.apply(lambda x: 'WRI' if x['PARTY']=='O' else x['LNAME'],axis=1)
election_sub.head()

County Election Date Precinct  Contest Group ID Contest Type  \
2      CRAVEN    11/03/2020       03            1293.0            S   
5     FORSYTH    11/03/2020      501            1322.0            S   
35  GRANVILLE    11/03/2020     SOOX            1201.0            S   
36     GASTON    11/03/2020       10            1278.0            S   
38   MCDOWELL    11/03/2020    MAR 3            1413.0            S   

                                Contest Name          Choice Choice Party  \
2                NC STATE SENATE DISTRICT 02  Libbie Griffin          DEM   
5                NC STATE SENATE DISTRICT 31   Joyce Krawiec          REP   
35  NC HOUSE OF REPRESENTATIVES DISTRICT 032   David Woodson          REP   
36  NC HOUSE OF REPRESENTATIVES DISTRICT 109     Susan Maxon          DEM   
38   US HOUSE OF REPRESENTATIVES DISTRICT 11  Tracey DeBruhl          LIB   

    Vote For  Election Day  One Stop  Absentee by Mail  Provisional  \
2        1.0          60.0     494.0             266.0          2.0   
5        1.0          27.0      93.0              18.0          2.0   
35       1.0          47.0     161.0              33.0          1.0   
36       1.0         109.0     630.0             230.0          2.0   
38       1.0           5.0       8.0               2.0          0.0   

    Total Votes Real Precinct  Unnamed: 15 PARTY LEVEL LASTNAME RESTNAME  \
2           822             Y          NaN     D    SU  Griffin  Libbie    
5           140             Y          NaN     R    SU  Krawiec   Joyce    
35          242             Y          NaN     R    SL  Woodson   David    
36          971             Y          NaN     D    SL    Maxon   Susan    
38           15             Y          NaN     L   CON  DeBruhl  Tracey    

           WHOLENAME PARTY3                                   CONTEST  \
2   Griffin, Libbie   (DEM)               NC STATE SENATE DISTRICT 02   
5    Krawiec, Joyce   (REP)               NC STATE SENATE DISTRICT 31   
35   Woodson, David   (REP)  NC HOUSE OF REPRESENTATIVES DISTRICT 032   
36     Maxon, Susan   (DEM)  NC HOUSE OF REPRESENTATIVES DISTRICT 109   
38  DeBruhl, Tracey   (LIB)   US HOUSE OF REPRESENTATIVES DISTRICT 11   

                NAME_PARTY                                         FIELDS_VAL  \
2   Griffin, Libbie  (DEM)  Griffin, Libbie  (DEM), NC STATE SENATE DISTRI...   
5    Krawiec, Joyce  (REP)  Krawiec, Joyce  (REP), NC STATE SENATE DISTRIC...   
35   Woodson, David  (REP)  Woodson, David  (REP), NC HOUSE OF REPRESENTAT...   
36     Maxon, Susan  (DEM)  Maxon, Susan  (DEM), NC HOUSE OF REPRESENTATIV...   
38  DeBruhl, Tracey  (LIB)  DeBruhl, Tracey  (LIB), US HOUSE OF REPRESENTA...   

   LNAME  
2    GRI  
5    KRA  
35   WOO  
36   MAX  
38   DEB

### Add district assignment field

In [17]:
election_sub['DIST'] = election_sub['Contest Name'].apply(lambda x: x.split(' ')[-1])
election_sub.head()

County Election Date Precinct  Contest Group ID Contest Type  \
2      CRAVEN    11/03/2020       03            1293.0            S   
5     FORSYTH    11/03/2020      501            1322.0            S   
35  GRANVILLE    11/03/2020     SOOX            1201.0            S   
36     GASTON    11/03/2020       10            1278.0            S   
38   MCDOWELL    11/03/2020    MAR 3            1413.0            S   

                                Contest Name          Choice Choice Party  \
2                NC STATE SENATE DISTRICT 02  Libbie Griffin          DEM   
5                NC STATE SENATE DISTRICT 31   Joyce Krawiec          REP   
35  NC HOUSE OF REPRESENTATIVES DISTRICT 032   David Woodson          REP   
36  NC HOUSE OF REPRESENTATIVES DISTRICT 109     Susan Maxon          DEM   
38   US HOUSE OF REPRESENTATIVES DISTRICT 11  Tracey DeBruhl          LIB   

    Vote For  Election Day  One Stop  Absentee by Mail  Provisional  \
2        1.0          60.0     494.0             266.0          2.0   
5        1.0          27.0      93.0              18.0          2.0   
35       1.0          47.0     161.0              33.0          1.0   
36       1.0         109.0     630.0             230.0          2.0   
38       1.0           5.0       8.0               2.0          0.0   

    Total Votes Real Precinct  Unnamed: 15 PARTY LEVEL LASTNAME RESTNAME  \
2           822             Y          NaN     D    SU  Griffin  Libbie    
5           140             Y          NaN     R    SU  Krawiec   Joyce    
35          242             Y          NaN     R    SL  Woodson   David    
36          971             Y          NaN     D    SL    Maxon   Susan    
38           15             Y          NaN     L   CON  DeBruhl  Tracey    

           WHOLENAME PARTY3                                   CONTEST  \
2   Griffin, Libbie   (DEM)               NC STATE SENATE DISTRICT 02   
5    Krawiec, Joyce   (REP)               NC STATE SENATE DISTRICT 31   
35   Woodson, David   (REP)  NC HOUSE OF REPRESENTATIVES DISTRICT 032   
36     Maxon, Susan   (DEM)  NC HOUSE OF REPRESENTATIVES DISTRICT 109   
38  DeBruhl, Tracey   (LIB)   US HOUSE OF REPRESENTATIVES DISTRICT 11   

                NAME_PARTY                                         FIELDS_VAL  \
2   Griffin, Libbie  (DEM)  Griffin, Libbie  (DEM), NC STATE SENATE DISTRI...   
5    Krawiec, Joyce  (REP)  Krawiec, Joyce  (REP), NC STATE SENATE DISTRIC...   
35   Woodson, David  (REP)  Woodson, David  (REP), NC HOUSE OF REPRESENTAT...   
36     Maxon, Susan  (DEM)  Maxon, Susan  (DEM), NC HOUSE OF REPRESENTATIV...   
38  DeBruhl, Tracey  (LIB)  DeBruhl, Tracey  (LIB), US HOUSE OF REPRESENTA...   

   LNAME DIST  
2    GRI   02  
5    KRA   31  
35   WOO  032  
36   MAX  109  
38   DEB   11

## Pivot the data

### Create pivot column and unique precinct ID

In [18]:
election_sub['PIVOT_COL'] = election_sub.apply(lambda x: ''.join(['G',x['LEVEL'],x['DIST'],x['PARTY'],x['LNAME']]),axis=1)
fields_dict = dict(zip(list(election_sub['PIVOT_COL']),list(election_sub['FIELDS_VAL'])))
election_sub['prec_field'] = election_sub.apply(lambda x: '_'.join([x['Precinct'],x['County']]),axis=1)
election_sub.head()

County Election Date Precinct  Contest Group ID Contest Type  \
2      CRAVEN    11/03/2020       03            1293.0            S   
5     FORSYTH    11/03/2020      501            1322.0            S   
35  GRANVILLE    11/03/2020     SOOX            1201.0            S   
36     GASTON    11/03/2020       10            1278.0            S   
38   MCDOWELL    11/03/2020    MAR 3            1413.0            S   

                                Contest Name          Choice Choice Party  \
2                NC STATE SENATE DISTRICT 02  Libbie Griffin          DEM   
5                NC STATE SENATE DISTRICT 31   Joyce Krawiec          REP   
35  NC HOUSE OF REPRESENTATIVES DISTRICT 032   David Woodson          REP   
36  NC HOUSE OF REPRESENTATIVES DISTRICT 109     Susan Maxon          DEM   
38   US HOUSE OF REPRESENTATIVES DISTRICT 11  Tracey DeBruhl          LIB   

    Vote For  Election Day  One Stop  Absentee by Mail  Provisional  \
2        1.0          60.0     494.0             266.0          2.0   
5        1.0          27.0      93.0              18.0          2.0   
35       1.0          47.0     161.0              33.0          1.0   
36       1.0         109.0     630.0             230.0          2.0   
38       1.0           5.0       8.0               2.0          0.0   

    Total Votes Real Precinct  Unnamed: 15 PARTY LEVEL LASTNAME RESTNAME  \
2           822             Y          NaN     D    SU  Griffin  Libbie    
5           140             Y          NaN     R    SU  Krawiec   Joyce    
35          242             Y          NaN     R    SL  Woodson   David    
36          971             Y          NaN     D    SL    Maxon   Susan    
38           15             Y          NaN     L   CON  DeBruhl  Tracey    

           WHOLENAME PARTY3                                   CONTEST  \
2   Griffin, Libbie   (DEM)               NC STATE SENATE DISTRICT 02   
5    Krawiec, Joyce   (REP)               NC STATE SENATE DISTRICT 31   
35   Woodson, David   (REP)  NC HOUSE OF REPRESENTATIVES DISTRICT 032   
36     Maxon, Susan   (DEM)  NC HOUSE OF REPRESENTATIVES DISTRICT 109   
38  DeBruhl, Tracey   (LIB)   US HOUSE OF REPRESENTATIVES DISTRICT 11   

                NAME_PARTY                                         FIELDS_VAL  \
2   Griffin, Libbie  (DEM)  Griffin, Libbie  (DEM), NC STATE SENATE DISTRI...   
5    Krawiec, Joyce  (REP)  Krawiec, Joyce  (REP), NC STATE SENATE DISTRIC...   
35   Woodson, David  (REP)  Woodson, David  (REP), NC HOUSE OF REPRESENTAT...   
36     Maxon, Susan  (DEM)  Maxon, Susan  (DEM), NC HOUSE OF REPRESENTATIV...   
38  DeBruhl, Tracey  (LIB)  DeBruhl, Tracey  (LIB), US HOUSE OF REPRESENTA...   

   LNAME DIST   PIVOT_COL      prec_field  
2    GRI   02   GSU02DGRI       03_CRAVEN  
5    KRA   31   GSU31RKRA     501_FORSYTH  
35   WOO  032  GSL032RWOO  SOOX_GRANVILLE  
36   MAX  109  GSL109DMAX       10_GASTON  
38   DEB   11  GCON11LDEB  MAR 3_MCDOWELL

### Pivot

In [19]:
pivoted_election_results = pd.pivot_table(election_sub,values=["Total Votes"],index=["prec_field"],columns=["PIVOT_COL"],aggfunc=sum)
pivoted_election_results.head()

Total Votes                                              \
PIVOT_COL    GCON01DBUT GCON01RSMI GCON02DROS GCON02LMAT GCON02RSWA   
prec_field                                                            
0001_BURKE          NaN        NaN        NaN        NaN        NaN   
0003_BURKE          NaN        NaN        NaN        NaN        NaN   
0003_STANLY         NaN        NaN        NaN        NaN        NaN   
0007_STANLY         NaN        NaN        NaN        NaN        NaN   
0008_STANLY         NaN        NaN        NaN        NaN        NaN   

                                                                               \
PIVOT_COL   GCON03DFAR GCON03RMUR GCON04DPRI GCON04RTHO GCON05CGRE GCON05DBRO   
prec_field                                                                      
0001_BURKE         NaN        NaN        NaN        NaN       47.0      662.0   
0003_BURKE         NaN        NaN        NaN        NaN        9.0      191.0   
0003_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0007_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0008_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   

                                                                               \
PIVOT_COL   GCON05RFOX GCON06DMAN GCON06RHAY GCON07DWAR GCON07OWRI GCON07RROU   
prec_field                                                                      
0001_BURKE      1609.0        NaN        NaN        NaN        NaN        NaN   
0003_BURKE       672.0        NaN        NaN        NaN        NaN        NaN   
0003_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0007_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0008_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   

                                                                               \
PIVOT_COL   GCON08DTIM GCON08RHUD GCON09DWAL GCON09RBIS GCON10DPAR GCON10RMCH   
prec_field                                                                      
0001_BURKE         NaN        NaN        NaN        NaN        NaN        NaN   
0003_BURKE         NaN        NaN        NaN        NaN        NaN        NaN   
0003_STANLY      736.0      989.0        NaN        NaN        NaN        NaN   
0007_STANLY      614.0     1062.0        NaN        NaN        NaN        NaN   
0008_STANLY      913.0      155.0        NaN        NaN        NaN        NaN   

                                                                               \
PIVOT_COL   GCON11DDAV GCON11GZWI GCON11LDEB GCON11RCAW GCON12DADA GCON13DHUF   
prec_field                                                                      
0001_BURKE         NaN        NaN        NaN        NaN        NaN        NaN   
0003_BURKE         NaN        NaN        NaN        NaN        NaN        NaN   
0003_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0007_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0008_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   

                                                                               \
PIVOT_COL   GCON13RBUD GSL001DNIC GSL001RGOO GSL002DDEP GSL002RYAR GSL003DWHI   
prec_field                                                                      
0001_BURKE         NaN        NaN        NaN        NaN        NaN        NaN   
0003_BURKE         NaN        NaN        NaN        NaN        NaN        NaN   
0003_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0007_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   
0008_STANLY        NaN        NaN        NaN        NaN        NaN        NaN   

                                                                               \
PIVOT_COL   GSL003RTYS GSL004DSCH GSL004RDIX GSL005DHUN GSL005RKIR GSL006DFUL   
prec_field                          

### Clean the pivoted data

In [20]:
#Fill in N/A with 0
pivoted_election_results = pivoted_election_results.fillna(0)

#Clean the columns
pivoted_election_results.reset_index(drop=False,inplace=True)
pivoted_election_results.columns = pivoted_election_results.columns.droplevel(0)
pivoted_election_results.rename(columns={pivoted_election_results.columns[0]: 'PREC_CO'},inplace=True)
pivoted_election_results['PRECINCT'] = pivoted_election_results['PREC_CO'].apply(lambda x: x.split('_')[0])
pivoted_election_results['COUNTY'] = pivoted_election_results['PREC_CO'].apply(lambda x: x.split('_')[1])
pivoted_election_results.head()

PIVOT_COL      PREC_CO  GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  \
0           0001_BURKE         0.0         0.0         0.0         0.0   
1           0003_BURKE         0.0         0.0         0.0         0.0   
2          0003_STANLY         0.0         0.0         0.0         0.0   
3          0007_STANLY         0.0         0.0         0.0         0.0   
4          0008_STANLY         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON02RSWA  GCON03DFAR  GCON03RMUR  GCON04DPRI  GCON04RTHO  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON05CGRE  GCON05DBRO  GCON05RFOX  GCON06DMAN  GCON06RHAY  \
0                47.0       662.0      1609.0         0.0         0.0   
1                 9.0       191.0       672.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON07DWAR  GCON07OWRI  GCON07RROU  GCON08DTIM  GCON08RHUD  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0       736.0       989.0   
3                 0.0         0.0         0.0       614.0      1062.0   
4                 0.0         0.0         0.0       913.0       155.0   

PIVOT_COL  GCON09DWAL  GCON09RBIS  GCON10DPAR  GCON10RMCH  GCON11DDAV  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  GCON13DHUF  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON13RBUD  GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL003DWHI  GSL003RTYS  GSL004DSCH  GSL004RDIX  GSL005DHUN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL005RKIR  GSL006DFUL  GSL006RHAN  GSL007DSTO  GSL007RWIN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL008DSMI  GSL008RMOO  GSL009DF

## Allocate absentee votes

In [21]:
def allocate_absentee(df_receiving_votes,df_allocating,column_list,col_allocating):
    original_cols = list(df_receiving_votes.columns)
    
    #Add in the "Total Votes column"
    df_receiving_votes.loc[:,"Total_Votes"]=0
    for race in column_list:
        df_receiving_votes.loc[:,"Total_Votes"]+=df_receiving_votes.loc[:,race]
    
    #Create the needed dataframes
    precinct_specific_totals = pd.DataFrame(df_receiving_votes.groupby([col_allocating]).sum())
    precinct_specific_totals.reset_index(drop=False,inplace=True)
    to_dole_out_totals = pd.DataFrame(df_allocating.groupby([col_allocating]).sum())
    to_dole_out_totals.reset_index(drop=False,inplace=True)
    
    #Print out any instances where the allocation, as written, won't work
    special_allocation_needed = []
    for index, row in precinct_specific_totals.iterrows():
        for race in column_list:
            if (row[race]==0):
                race_district = row[col_allocating]
                if race_district in to_dole_out_totals[col_allocating].unique():
                    to_allocate = int(to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==race_district][race])
                    if (to_allocate != 0):
                        special_allocation_needed.append([race_district,race])
    
    #Create some new columns for each of these races to deal with the allocation
    for race in column_list:
        add_var = race+"_add"
        rem_var = race+"_rem"
        floor_var = race+"_floor"
        df_receiving_votes.loc[:,add_var]=0.0
        df_receiving_votes.loc[:,rem_var]=0.0
        df_receiving_votes.loc[:,floor_var]=0.0

    #Iterate over the rows
    #Note this function iterates over the dataframe two times so the rounded vote totals match the totals to allocate
    for index, row in df_receiving_votes.iterrows():
        if row[col_allocating] in to_dole_out_totals[col_allocating].unique():
            for race in column_list:
                add_var = race+"_add"
                rem_var = race+"_rem"
                floor_var = race+"_floor"
                #Grab the district
                county_id = row[col_allocating]
                if [county_id,race] in special_allocation_needed:
                    #Get the denominator for the allocation - the summed "total votes" for precincts in that grouping
                    denom = precinct_specific_totals.loc[precinct_specific_totals[col_allocating]==county_id]["Total_Votes"]
                    #Get one of the numerators, how many districtwide votes to allocate
                    numer = to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==county_id][race]
                    #Get the "total votes" for this particular precinct
                    val = df_receiving_votes.at[index,"Total_Votes"]
                    #Get the vote share, the precincts % of total precinct votes in the district times votes to allocate
                else:
                    #Get the denominator for the allocation (the precinct vote totals)
                    denom = precinct_specific_totals.loc[precinct_specific_totals[col_allocating]==county_id][race]
                    #Get one of the numerators, how many districtwide votes to allocate
                    numer = to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==county_id][race]
                    #Get the vote totals for this race in this precinct
                    val = df_receiving_votes.at[index,race]
                    #Get the vote share, the precincts % of total precinct votes in the district times votes to allocate
                if ((float(denom)==0)):
                    vote_share = 0
                else:
                    vote_share = (float(val)/float(denom))*float(numer)
                df_receiving_votes.at[index,add_var] = vote_share
                #Take the decimal remainder of the allocation
                df_receiving_votes.at[index,rem_var] = vote_share%1
                #Take the floor of the allocation
                df_receiving_votes.at[index,floor_var] = np.floor(vote_share)

    #After the first pass through, get the sums of the races by district to assist in the rounding            
    first_allocation = pd.DataFrame(df_receiving_votes.groupby([col_allocating]).sum())

    #Now we want to iterate district by district to work on rounding
    county_list = list(to_dole_out_totals[col_allocating].unique()) 

    #Iterate over the district
    for county in county_list:
        for race in column_list:
            add_var = race+"_add"
            rem_var = race+"_rem"
            floor_var = race+"_floor"
            #County how many votes still need to be allocated (because we took the floor of all the initial allocations)
            to_go = int(np.round((int(to_dole_out_totals.loc[to_dole_out_totals[col_allocating]==county][race])-first_allocation.loc[first_allocation.index==county,floor_var])))
            #Grab the n precincts with the highest remainders and round these up, where n is the # of votes that still need to be allocated
            for index in df_receiving_votes.loc[df_receiving_votes[col_allocating]==county][rem_var].nlargest(to_go).index:
                df_receiving_votes.at[index,add_var] = np.ceil(df_receiving_votes.at[index,add_var])

    #Iterate over every race again
    for race in column_list:
        add_var = race+"_add"
        #Round every allocation down to not add fractional votes
        df_receiving_votes.loc[:,add_var]=np.floor(df_receiving_votes.loc[:,add_var])
        df_receiving_votes.loc[:,race]+=df_receiving_votes.loc[:,add_var]
        
    df_receiving_votes = df_receiving_votes[original_cols]
    
    return df_receiving_votes

### Create dataframe of votes to allocate

In [22]:
#List of non-physical precincts to remove for dataframe to allocate
searchfor = ['ABSENTEE', 'ONE STOP', 'ONE STOP ARB', 'ONE STOP BOE', 'ONE STOP CBC', 'ONE STOP CFC', 'ONE STOP CFN', 'ONE STOP GVT', 'ONE STOP HOS', 'ONE STOP MSL', 'ONE STOP NLB', 'ONE STOP PVL', 'ONE STOP SRC', 'PROVISIONAL', 'TRANSFER']
searchfor = searchfor+['OS AG CENTER','OS CJRC','OS COMM SCHOOLS','OS DUKE','OS ENO','OS EPPES','OS ERL','OS FARMVILLE','OS GETG','OS HVBC','OS ML','OS MSUMC','OS NCCU','OS NRL','OS SHS','OS SRL','OS STUDENT CENTER','OS TRC','OS WILLIS BUILDING','OS WINTERVILLE','ABSENTEE MAIL','ABSENTEE BY MAIL','ABSENTEE SUPPLEMENTAL','AVML','AVOM','AURORA OS','ARCHER LODGE','ELK OS','LINCOLN OS','BOE OS','BOE OFFICE','BMBL','PM OS']
searchfor = searchfor+['HACC', 'OS GASTON', 'BOOK T. WASHINGTON', 'OS TLIB', 'EAST ARCADIA', 'ONE STOP AG', 'MURFREE CNTR', 'OSCA 1-40', 'OS LITTLETON', 'ONE STOP VTH', 'OSKD 121-128', 'OSLL 1-40', 'OSWO 1-40', 'LSKY', 'OSAP 81-120', 'OS BOE', 'OSAP 41-80', 'OS RINGWOOD', 'OSWO 81-120', 'OS WARSAW', 'PROVI 1-40', 'CHOCO OS', 'BAY TREE FIRE DEPT', 'OS WW', 'OS LOB', 'OSAP 121-128', 'OSOP 81-120', 'OSBR 121-128', 'OS PHL', 'ONE STOP THREE', 'OSKD 41-80', 'OSBR 81-120', 'OS CARRBORO', 'FVCC', 'OSAB 121-128', 'OSRB 1-40', 'OSTA 1-40', 'ONE STOP ANNEX CONF RM', 'OS OCK', 'OSAV 121-128', 'OSLH 1-40', 'ONE STOP RS', 'SBBL', 'OS HALES', 'OSLH 41-80', 'BLAD COUNTY GYM', 'REYV', 'OS UM', 'OSWO 41-80', 'RMT 301 OS', 'OS MAX', 'OSAV 81-120', 'NASHVILLE OS', 'OSGR 81-120', 'CLEVELAND', 'CLAYTON', 'OSTA 121-128', 'WEST OS', 'OS ETOWAH', 'ONE STOP TWO', 'OSOP 1-40', 'ONE STOP KING', 'OSNR 41-80', 'OSRB 81-120', 'PROVI 121-128', 'OS RICHSQUARE', 'SPAULDING MONROE', 'OSCS 81-120', 'CO OP', 'OSOP 41-80', 'RMT DOWNTOWN OS', 'OS MOT', 'OSWN 81-120', 'OSZB 41-80', 'OSWN 41-80', 'OSNR 1-40', 'OS FLAT ROCK', 'OSLL 121-128', 'OS SEVERN', 'OS RESOURCE CENTER', 'MT. PLEASANT OS', 'OSAV 41-80', 'SELMA', 'TRANS 1-40', 'OS SEYMOUR', 'OS HAR', 'OS MCSWAIN', 'OSZB 81-120', 'ONE-STOP', 'UNCA', 'OSNR 121-128', 'OS CAE', 'OS MIDWAY FIRE DEPT', 'OS SCOTLAND NECK', 'OSCM 41-80', 'OS EFLAND', 'DET OF SOCIAL SERVICES', 'OSCA 121-128', 'OSWA 41-80', 'OSRB 41-80', 'BTFD', 'OSHS 1-40', 'MA OS', 'ONE STOP DANBURY', 'OSWA 81-120', 'OSAP 1-40', 'TRANS 121-128', 'WVTH', 'OSCM 1-40', 'ONE STOP PCC', 'WACC', 'OS LIB', 'BROWDER', 'OS WESTERN', 'OS WALLACE', 'OSCS 1-40', 'MAIL ABSENTEE', 'LECC', 'OS DG', 'OSLH 81-120', 'OSNR 81-120', 'OSKD 1-40', 'OSRB 121-128', 'OS DENTON LIBRARY', 'OS POW', 'ABSEN 121-128', 'OS KTD', 'OS BOE', 'EAST OS', 'OSKD 81-120', 'OS COTC', 'OS FLETCHER', 'OSAB 81-120', 'TRANS 41-80', 'OSAV 1-40', 'OS ANGIER', 'OSAB 1-40', 'ECBL', 'OSHS 81-120', 'TAR HEEL MUNI BLD', 'ABSEN 1-40', 'OS BOE', 'OSBR 1-40', 'OS ARCADIA COMM BLDG', 'OSLL 81-120', 'OSWA 1-40', 'PROVIDENCE', 'CITY OS', 'OSLL 41-80', 'OSGR 121-128', 'OS ADMIN', 'OSAB 41-80', 'ELLERBE', 'OSGR 41-80', 'ABSEN 81-120', 'DOB OS', 'OS BR', 'ABSEN 41-80', 'OSWO 121-128', 'TRANS 81-120', 'OSCA 41-80', 'OSCA 81-120', 'OSWN 121-128', 'OSCS 121-128', 'ONE STOP ONE', 'OS ASU', 'OSBR 41-80', 'OSGR 1-40', 'HAMLET', 'OSHS 121-128', 'OSHS 41-80', 'OS NTP', 'OS LW', 'TARBORO 1', 'BELHAVEN OS', 'OSCM 81-120', 'OSTA 41-80', 'SMITHFIELD', 'OS LOBBY', 'OSLH 121-128', 'OSTA 81-120', 'OSOP 121-128', 'OSCM 121-128', 'OSZB 121-128', 'OSZB 1-40', 'PINES CHAP FELLSHIP HALL', 'OSCS 41-80', 'OS FSCO', 'OS ERWIN', 'OS BCR', 'OS GRANITE REC', 'WGSC', 'BENSON', 'OSWA 121-128', 'OSWN 1-40', 'PROVI 41-80', 'PROVI 81-120', 'OS BOE']
searchfor = searchfor+['MCGEE OS','OFFICE OS','ONE STOP CBR','ONE STOP EES']
searchfor = searchfor+['OS KENANSVILLE','OS JACKSON','OS HALIFAX','OS DTM','ONE STOP WALNUT COVE']

In [23]:
#Subset the data
in_sos =  pivoted_election_results[pivoted_election_results["PRECINCT"].isin(searchfor)]
#Add a particular precinct to the votes to allocate (it's precinct name is the same as one in another county, and that one is a real precinct)
buncombe_tcrk = pivoted_election_results[pivoted_election_results["PREC_CO"]=='TCRK_BUNCOMBE']
in_sos = pd.concat([in_sos,buncombe_tcrk])
in_sos = in_sos.groupby(by=["COUNTY"]).sum().reset_index()
display(in_sos)

PIVOT_COL       COUNTY  GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  \
0             ALAMANCE         0.0         0.0         0.0         0.0   
1            ALLEGHANY         0.0         0.0         0.0         0.0   
2                 ASHE         0.0         0.0         0.0         0.0   
3                AVERY         0.0         0.0         0.0         0.0   
4             BEAUFORT         0.0         0.0         0.0         0.0   
5               BERTIE        27.0         8.0         0.0         0.0   
6               BLADEN         0.0         0.0         0.0         0.0   
7             BUNCOMBE         0.0         0.0         0.0         0.0   
8             CABARRUS         0.0         0.0         0.0         0.0   
9             CALDWELL         0.0         0.0         0.0         0.0   
10              CAMDEN         0.0         0.0         0.0         0.0   
11           CURRITUCK         0.0         0.0         0.0         0.0   
12                DARE         0.0         0.0         0.0         0.0   
13            DAVIDSON         0.0         0.0         0.0         0.0   
14               DAVIE         0.0         0.0         0.0         0.0   
15              DUPLIN         0.0         0.0         0.0         0.0   
16              DURHAM         0.0         0.0         0.0         0.0   
17           EDGECOMBE         0.0         0.0         0.0         0.0   
18            GUILFORD         0.0         0.0         0.0         0.0   
19             HALIFAX      1862.0       302.0         0.0         0.0   
20             HARNETT         0.0         0.0         0.0         0.0   
21             HAYWOOD         0.0         0.0         0.0         0.0   
22           HENDERSON         0.0         0.0         0.0         0.0   
23            HERTFORD         0.0         0.0         0.0         0.0   
24                HYDE         0.0         0.0         0.0         0.0   
25            JOHNSTON         0.0         0.0         0.0         0.0   
26               JONES         0.0         0.0         0.0         0.0   
27                 LEE         0.0         0.0         0.0         0.0   
28             LINCOLN         0.0         0.0         0.0         0.0   
29               MACON         0.0         0.0         0.0         0.0   
30              MARTIN        35.0        33.0         0.0         0.0   
31         MECKLENBURG         0.0         0.0         0.0         0.0   
32               MOORE         0.0         0.0         0.0         0.0   
33                NASH         0.0         0.0         0.0         0.0   
34         NEW HANOVER         0.0         0.0         0.0         0.0   
35         NORTHAMPTON        26.0         9.0         0.0         0.0   
36              ORANGE         0.0         0.0         0.0         0.0   
37          PASQUOTANK         0.0         0.0         0.0         0.0   
38                PITT       252.0       136.0         0.0         0.0   
39                POLK         0.0         0.0         0.0         0.0   
40            RICHMOND         0.0         0.0         0.0         0.0   
41            SCOTLAND         0.0         0.0         0.0         0.0   
42              STOKES         0.0         0.0         0.0         0.0   
43               SURRY         0.0         0.0         0.0         0.0   
44             TYRRELL         0.0         0.0         0.0         0.0   
45                WAKE         0.0         0.0         0.0         0.0   
46          WASHINGTON         0.0         0.0         0.0         0.0   
47             WATAUGA         0.0         0.0         0.0         0.0   
48               WAYNE         0.0         0.0         0.0         0.0   
49              WILKES         0.0         0.0         0.0         0.0   
50              YADKIN         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON02RSWA  GCON03DFAR  GCON03RMUR  GCON04DPRI  GCON04RTHO  \
0                 0.0         0.0         0.0         0.0         0.0   
1    

### Perform the allocation

In [24]:
pivoted_copy = pivoted_election_results
#Remove county-wide results
election_results = pivoted_election_results[~pivoted_election_results["PRECINCT"].isin(searchfor)]
#remove the one precicnt specified above
election_results = election_results[election_results['PREC_CO']!='TCRK_BUNCOMBE']

#identify candidate race columns
races = [x for x in pivoted_copy.columns if x.startswith('G')]
#allocation
election_results_allocated = allocate_absentee(election_results,in_sos,races,'COUNTY')
election_results_allocated.head()

C:\Users\SpencerNelson\Anaconda3\envs\rdh\lib\site-packages\pandas\core\indexing.py:1667: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self.obj[key] = value


PIVOT_COL      PREC_CO  GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  \
0           0001_BURKE         0.0         0.0         0.0         0.0   
1           0003_BURKE         0.0         0.0         0.0         0.0   
2          0003_STANLY         0.0         0.0         0.0         0.0   
3          0007_STANLY         0.0         0.0         0.0         0.0   
4          0008_STANLY         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON02RSWA  GCON03DFAR  GCON03RMUR  GCON04DPRI  GCON04RTHO  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON05CGRE  GCON05DBRO  GCON05RFOX  GCON06DMAN  GCON06RHAY  \
0                47.0       662.0      1609.0         0.0         0.0   
1                 9.0       191.0       672.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON07DWAR  GCON07OWRI  GCON07RROU  GCON08DTIM  GCON08RHUD  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0       736.0       989.0   
3                 0.0         0.0         0.0       614.0      1062.0   
4                 0.0         0.0         0.0       913.0       155.0   

PIVOT_COL  GCON09DWAL  GCON09RBIS  GCON10DPAR  GCON10RMCH  GCON11DDAV  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  GCON13DHUF  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON13RBUD  GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL003DWHI  GSL003RTYS  GSL004DSCH  GSL004RDIX  GSL005DHUN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL005RKIR  GSL006DFUL  GSL006RHAN  GSL007DSTO  GSL007RWIN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL008DSMI  GSL008RMOO  GSL009DF

In [25]:
#Set all to integer
for i in pivoted_copy.columns:
    if i.startswith('G'):
        pivoted_copy[i] = pivoted_copy[i].astype(int)

In [26]:
#Verify the length of the allocated dataframe with VEST's
print(len(election_results_allocated))
print(len(vest))

2662
2662


## Determine split precincts

In [27]:
#Instantiate variables
##DETERMINE WHAT PRECINCTS ARE SPLIT
er = election_results_allocated 
cong_splits = []
sldl_splits = []
sldu_splits = []
cong_split_count = 0
sldl_split_count = 0
sldu_split_count = 0
cong_split_dictionary = {}
sldu_split_dictionary = {}
sldl_split_dictionary = {}

cong_unsplit_dict = {}
sldu_unsplit_dict = {}
sldl_unsplit_dict = {}
no_dists = []

In [28]:
for i in er['PREC_CO']:
    sub = er[er['PREC_CO']==i]
    cong = []
    sldl = []
    sldu = []
    for col in sub.columns:
        if col.startswith('G'):
            col_sum = sub[col].sum()
            if int(col_sum)!= 0:
                if 'GCON' in str(col):
                    cong_dist = str(col).replace('GCON','')[:2]
                    cong.append(cong_dist)
                elif 'GSU' in str(col):
                    sldu_dist = str(col).replace('GSU','')[:2]
                    sldu.append(sldu_dist)
                else:
                    sldl_dist = str(col).replace('GSL','')[:3]
                    sldl.append(sldl_dist)
    cong = list(set(cong))
    sldl = list(set(sldl))
    sldu = list(set(sldu))
    if len(cong)>1:
        print(i, ' is split by congressional district. It is in districts: ', ', '.join(cong))
        cong_splits.append(i)
        cong_split_count+=1
        cong_split_dictionary.update({i:cong})
    if len(cong)==1:
        cong_unsplit_dict.update({i:cong[0]})
    if len(cong) == 0:
        no_dists.append(i)
    if len(sldl)> 1:
        print(i, ' is split by State House district. It is in districts: ', ', '.join(sldl))
        sldl_splits.append(i)
        sldl_split_count+=1
        sldl_split_dictionary.update({i:sldl})
    if len(sldl)==0:
        no_dists.append(i)
    if len(sldl)==1:
        sldl_unsplit_dict.update({i:sldl[0]})
    if len(sldu)> 1:
        print(i, ' is split by State Senate districts. It is in districts: ', ', '.join(sldu))
        sldu_splits.append(i)
        sldu_split_count+=1
        sldu_split_dictionary.update({i:sldu})
    if len(sldu)==0:
        no_dists.append(i)
    if len(sldu)==1:
        sldu_unsplit_dict.update({i:sldu[0]})
no_dists = list(set(no_dists))
print('****************************************************')
print('Congressional split count: ', str(cong_split_count))
print(cong_split_dictionary)
print('SLDU split count: ', str(sldu_split_count))
print(sldu_split_dictionary)
print('SLDL split count: ', str(sldl_split_count))
print(sldl_split_dictionary)
print('***************************************************')
print('There are NO districts associated with the following precincts: ', sorted(no_dists))
print('There are ', str(len(no_dists)), ' that are NOT assigned to a district.')
print('There are ', str(len(vest)), ' in the VEST file.')
print('There are ', str(len(er)), ' in the allocated election results file.')
diff = len(er)-len(vest)
if diff==len(no_dists):
    print('The no district list is same length as difference between ER and VEST: ', str(diff))
else:
    print('The no district lenght is: ', str(len(no_dists)))
    print('The difference between VEST and ER is: ', str(diff))
    print('The difference between the values is: ', str(diff-len(no_dists)))

03-00_WAKE  is split by State House district. It is in districts:  041, 037
04-08_WAKE  is split by State House district. It is in districts:  049, 041
04-16_WAKE  is split by State House district. It is in districts:  036, 011
04-18_WAKE  is split by State House district. It is in districts:  049, 041
04-19_WAKE  is split by State House district. It is in districts:  036, 041
05-07_WAKE  is split by State House district. It is in districts:  041, 040
0601_PITT  is split by congressional district. It is in districts:  01, 03
0601_PITT  is split by State House district. It is in districts:  012, 009
062_FORSYTH  is split by congressional district. It is in districts:  06, 10
07-10_WAKE  is split by State House district. It is in districts:  049, 040
08-02_WAKE  is split by State House district. It is in districts:  049, 040
08-10_WAKE  is split by State House district. It is in districts:  049, 040
096_MECKLENBURG  is split by congressional district. It is in districts:  09, 12
09_WAYNE

In [29]:
## Confirm that there are no precincts left that have no district assigned to them
no_dists_distribute = [i.split('_')[0] for i in no_dists]
print(no_dists_distribute)

[]


In [30]:
## Verify with VEST again
vest['MATCH'] = vest.apply(lambda x: '_'.join([x['PREC_ID'],x['COUNTY_NAM']]),axis=1)
er['MATCH'] = er['PREC_CO'].apply(lambda x: str(x))
join = pd.merge(vest,er, on = 'MATCH',how='outer',indicator=True)
print(len(join))
print(len(vest))
print(len(er))
print(join['_merge'].unique())

2662
2662
2662
['both']
Categories (3, object): ['left_only', 'right_only', 'both']


<ipython-input-30-3628a59c150b>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  er['MATCH'] = er['PREC_CO'].apply(lambda x: str(x))


### Separate the data into three dataframes

In [31]:
congress_cols = []
sldu_cols = []
sldl_cols = []
for i in er.columns:
    if i.startswith('GCON'):
        congress_cols.append(i)
    elif i.startswith('GS'):
        if i.startswith('GSU'):
            sldu_cols.append(i)
        else:
            sldl_cols.append(i)
    else:
        congress_cols.append(i)
        sldu_cols.append(i)
        sldl_cols.append(i)
cong_df = er[congress_cols]
sldu_df = er[sldu_cols]
sldl_df = er[sldl_cols]

display(cong_df.head())
display(sldu_df.head())
display(sldl_df.head())

PIVOT_COL      PREC_CO  GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  \
0           0001_BURKE         0.0         0.0         0.0         0.0   
1           0003_BURKE         0.0         0.0         0.0         0.0   
2          0003_STANLY         0.0         0.0         0.0         0.0   
3          0007_STANLY         0.0         0.0         0.0         0.0   
4          0008_STANLY         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON02RSWA  GCON03DFAR  GCON03RMUR  GCON04DPRI  GCON04RTHO  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON05CGRE  GCON05DBRO  GCON05RFOX  GCON06DMAN  GCON06RHAY  \
0                47.0       662.0      1609.0         0.0         0.0   
1                 9.0       191.0       672.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON07DWAR  GCON07OWRI  GCON07RROU  GCON08DTIM  GCON08RHUD  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0       736.0       989.0   
3                 0.0         0.0         0.0       614.0      1062.0   
4                 0.0         0.0         0.0       913.0       155.0   

PIVOT_COL  GCON09DWAL  GCON09RBIS  GCON10DPAR  GCON10RMCH  GCON11DDAV  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  GCON13DHUF  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON13RBUD PRECINCT  COUNTY        MATCH  
0                 0.0     0001   BURKE   0001_BURKE  
1                 0.0     0003   BURKE   0003_BURKE  
2                 0.0     0003  STANLY  0003_STANLY  
3                 0.0     0007  STANLY  0007_STANLY  
4                 0.0     0008  STANLY  0008_STANLY

PIVOT_COL      PREC_CO  GSU01DJUD  GSU01RSTE  GSU02DGRI  GSU02LHAR  GSU02RSAN  \
0           0001_BURKE        0.0        0.0        0.0        0.0        0.0   
1           0003_BURKE        0.0        0.0        0.0        0.0        0.0   
2          0003_STANLY        0.0        0.0        0.0        0.0        0.0   
3          0007_STANLY        0.0        0.0        0.0        0.0        0.0   
4          0008_STANLY        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU03DBAZ  GSU03RHES  GSU04DFIT  GSU04RWEB  GSU05DDAV  GSU05RKOZ  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU06DJOH  GSU06RLAZ  GSU07DLAK  GSU07RPER  GSU08DSIN  GSU08LMAS  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU08RRAB  GSU09DPET  GSU09RLEE  GSU10DMOO  GSU10RJAC  GSU11DWEL  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU11RBAR  GSU12DKIR  GSU12RBUR  GSU13DYAT  GSU13RBRI  GSU14DBLU  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU14LWAL  GSU14RMIC  GSU15DCHA  GSU15LMCD  GSU15RLOM  GSU16DNIC  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU16RMAR  GSU17DSEA  GSU17LGRO  GSU17RCAV  GSU18DCRA  GSU18LLOE  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU18RNOR  GSU19DDEV  GSU19RMER  GSU20DMUR  GSU20RTAR  GSU21DCLA  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU21RPAL  GSU22DWOO  GSU22LUBI  GSU22RPAD  GSU23DFOU  GSU23RGLE  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.

PIVOT_COL      PREC_CO  GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  \
0           0001_BURKE         0.0         0.0         0.0         0.0   
1           0003_BURKE         0.0         0.0         0.0         0.0   
2          0003_STANLY         0.0         0.0         0.0         0.0   
3          0007_STANLY         0.0         0.0         0.0         0.0   
4          0008_STANLY         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL003DWHI  GSL003RTYS  GSL004DSCH  GSL004RDIX  GSL005DHUN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL005RKIR  GSL006DFUL  GSL006RHAN  GSL007DSTO  GSL007RWIN  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL008DSMI  GSL008RMOO  GSL009DFAR  GSL009RJON  GSL010DMAR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL010RBEL  GSL011DDAH  GSL011LTRA  GSL011RPOP  GSL012DCOX  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  GSL014RCLE  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL015DGOM  GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL017RILE  GSL018DBUT  GSL018RKEN  GSL019DMOR  GSL019RMIL  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL020DERI  GSL020RDAV  GSL021DSMI  GSL021RHEA  GSL022DKIR  \
0                 0.0         0.0         0.0         0.0         0.0   
1                 0.0         0.0         0.0         0.0         0.0   
2                 0.0         0.0         0.0         0.0         0.0   
3                 0.0         0.0         0.0         0.0         0.0   
4                 0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL022RBRI  GSL023DWIL  GSL023GL

## Process State Senate file

In [32]:
sldu_df['SLDU_DIST'] = sldu_df['PREC_CO'].apply(lambda x: sldu_unsplit_dict.get(x))
sldu_df.head()

<ipython-input-32-53e1f1dc68a3>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sldu_df['SLDU_DIST'] = sldu_df['PREC_CO'].apply(lambda x: sldu_unsplit_dict.get(x))


PIVOT_COL      PREC_CO  GSU01DJUD  GSU01RSTE  GSU02DGRI  GSU02LHAR  GSU02RSAN  \
0           0001_BURKE        0.0        0.0        0.0        0.0        0.0   
1           0003_BURKE        0.0        0.0        0.0        0.0        0.0   
2          0003_STANLY        0.0        0.0        0.0        0.0        0.0   
3          0007_STANLY        0.0        0.0        0.0        0.0        0.0   
4          0008_STANLY        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU03DBAZ  GSU03RHES  GSU04DFIT  GSU04RWEB  GSU05DDAV  GSU05RKOZ  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU06DJOH  GSU06RLAZ  GSU07DLAK  GSU07RPER  GSU08DSIN  GSU08LMAS  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU08RRAB  GSU09DPET  GSU09RLEE  GSU10DMOO  GSU10RJAC  GSU11DWEL  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU11RBAR  GSU12DKIR  GSU12RBUR  GSU13DYAT  GSU13RBRI  GSU14DBLU  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU14LWAL  GSU14RMIC  GSU15DCHA  GSU15LMCD  GSU15RLOM  GSU16DNIC  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU16RMAR  GSU17DSEA  GSU17LGRO  GSU17RCAV  GSU18DCRA  GSU18LLOE  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU18RNOR  GSU19DDEV  GSU19RMER  GSU20DMUR  GSU20RTAR  GSU21DCLA  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.0        0.0        0.0        0.0        0.0   
2                0.0        0.0        0.0        0.0        0.0        0.0   
3                0.0        0.0        0.0        0.0        0.0        0.0   
4                0.0        0.0        0.0        0.0        0.0        0.0   

PIVOT_COL  GSU21RPAL  GSU22DWOO  GSU22LUBI  GSU22RPAD  GSU23DFOU  GSU23RGLE  \
0                0.0        0.0        0.0        0.0        0.0        0.0   
1                0.0        0.

In [33]:
for i in sldu_df.columns:
    if i.startswith('G'):
        sldu_df[i] = sldu_df[i].astype(int)
sldu_df.head()

<ipython-input-33-70f1ce69df35>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sldu_df[i] = sldu_df[i].astype(int)


PIVOT_COL      PREC_CO  GSU01DJUD  GSU01RSTE  GSU02DGRI  GSU02LHAR  GSU02RSAN  \
0           0001_BURKE          0          0          0          0          0   
1           0003_BURKE          0          0          0          0          0   
2          0003_STANLY          0          0          0          0          0   
3          0007_STANLY          0          0          0          0          0   
4          0008_STANLY          0          0          0          0          0   

PIVOT_COL  GSU03DBAZ  GSU03RHES  GSU04DFIT  GSU04RWEB  GSU05DDAV  GSU05RKOZ  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU06DJOH  GSU06RLAZ  GSU07DLAK  GSU07RPER  GSU08DSIN  GSU08LMAS  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU08RRAB  GSU09DPET  GSU09RLEE  GSU10DMOO  GSU10RJAC  GSU11DWEL  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU11RBAR  GSU12DKIR  GSU12RBUR  GSU13DYAT  GSU13RBRI  GSU14DBLU  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU14LWAL  GSU14RMIC  GSU15DCHA  GSU15LMCD  GSU15RLOM  GSU16DNIC  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU16RMAR  GSU17DSEA  GSU17LGRO  GSU17RCAV  GSU18DCRA  GSU18LLOE  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU18RNOR  GSU19DDEV  GSU19RMER  GSU20DMUR  GSU20RTAR  GSU21DCLA  \
0                  0          0          0          0          0          0   
1                  0          0          0          0          0          0   
2                  0          0          0          0          0          0   
3                  0          0          0          0          0          0   
4                  0          0          0          0          0          0   

PIVOT_COL  GSU21RPAL  GSU22DWOO  GSU22LUBI  GSU22RPAD  GSU23DFOU  GSU23RGLE  \
0                  0          0          0          0          0          0   
1                  0          

In [34]:
vest['COUNTY_ID'] = vest['COUNTY_ID'].astype(str)

In [35]:
sldu_vest = pd.merge(vest,sldu_df,on='MATCH',how = 'outer', indicator = True)
display(sldu_vest[sldu_vest['_merge']!='both'])

Empty GeoDataFrame
Columns: [PREC_ID, ENR_DESC, COUNTY_NAM, COUNTY_ID, G20PRERTRU, G20PREDBID, G20PRELJOR, G20PREGHAW, G20PRECBLA, G20PREOWRI, G20USSRTIL, G20USSDCUN, G20USSLBRA, G20USSCHAY, G20GOVRFOR, G20GOVDCOO, G20GOVLDIF, G20GOVCPIS, G20LTGRROB, G20LTGDHOL, G20ATGRONE, G20ATGDSTE, G20TRERFOL, G20TREDCHA, G20SOSRSYK, G20SOSDMAR, G20AUDRSTR, G20AUDDWOO, G20AGRRTRO, G20AGRDWAD, G20INSRCAU, G20INSDGOO, G20LABRDOB, G20LABDHOL, G20SPIRTRU, G20SPIDMAN, G20SSCRNEW, G20SSCDBEA, G20SSCRBER, G20SSCDINM, G20SSCRBAR, G20SSCDDAV, G20SACRWOO, G20SACDSHI, G20SACRGOR, G20SACDCUB, G20SACRDIL, G20SACDSTY, G20SACRCAR, G20SACDYOU, G20SACRGRI, G20SACDBRO, geometry, MATCH, PREC_CO, GSU01DJUD, GSU01RSTE, GSU02DGRI, GSU02LHAR, GSU02RSAN, GSU03DBAZ, GSU03RHES, GSU04DFIT, GSU04RWEB, GSU05DDAV, GSU05RKOZ, GSU06DJOH, GSU06RLAZ, GSU07DLAK, GSU07RPER, GSU08DSIN, GSU08LMAS, GSU08RRAB, GSU09DPET, GSU09RLEE, GSU10DMOO, GSU10RJAC, GSU11DWEL, GSU11RBAR, GSU12DKIR, GSU12RBUR, GSU13DYAT, GSU13RBRI, GSU14DBLU, GSU14LWAL, GSU14RMIC, GSU15DCHA, GSU15LMCD, GSU15RLOM, GSU16DNIC, GSU16RMAR, GSU17DSEA, GSU17LGRO, GSU17RCAV, GSU18DCRA, GSU18LLOE, GSU18RNOR, GSU19DDEV, GSU19RMER, GSU20DMUR, ...]
Index: []

In [36]:
sldu_vest.drop(columns = ['PREC_CO','PRECINCT','COUNTY','_merge'],inplace=True)
sldu_vest.rename(columns={'MATCH':'UNIQUE_ID'},inplace=True)
sldu_vest['COUNTY_ID'] = sldu_vest['COUNTY_ID'].astype(str)
sldu_vest['COUNTYFP'] = sldu_vest['COUNTY_ID'].apply(lambda x: str(x).zfill(3))
sldu_vest.head()

PREC_ID   ENR_DESC   COUNTY_NAM COUNTY_ID  G20PRERTRU  G20PREDBID  \
0      01  PATTERSON     ALAMANCE         1        2299         566   
1      02      COBLE     ALAMANCE         1        2387         559   
2      07   ALBRIGHT     ALAMANCE         1        1996         581   
3     H08        H08     GUILFORD        41          73         614   
4     079        079  MECKLENBURG        60         469        1223   

   G20PRELJOR  G20PREGHAW  G20PRECBLA  G20PREOWRI  G20USSRTIL  G20USSDCUN  \
0          27           6           5           4        2205         564   
1          15           4           4           3        2290         570   
2          20           9           1           4        1917         588   
3           3           1           2           2          70         595   
4           8           9           2           6         418        1190   

   G20USSLBRA  G20USSCHAY  G20GOVRFOR  G20GOVDCOO  G20GOVLDIF  G20GOVCPIS  \
0          68          51        2209         661          19          13   
1          65          32        2264         677          18           9   
2          63          23        1936         644          19           3   
3          11          12          63         621           3           6   
4          64          29         418        1250          33          17   

   G20LTGRROB  G20LTGDHOL  G20ATGRONE  G20ATGDSTE  G20TRERFOL  G20TREDCHA  \
0        2336         556        2266         618        2240         611   
1        2391         556        2323         614        2319         603   
2        2013         578        1957         616        1968         595   
3          76         615          79         611          89         598   
4         460        1232         443        1244         495        1182   

   G20SOSRSYK  G20SOSDMAR  G20AUDRSTR  G20AUDDWOO  G20AGRRTRO  G20AGRDWAD  \
0        2251         617        2247         608        2401         485   
1        2270         663        2301         612        2468         472   
2        1903         659        1927         629        2078         502   
3          67         617          77         610          76         613   
4         427        1259         443        1236         454        1230   

   G20INSRCAU  G20INSDGOO  G20LABRDOB  G20LABDHOL  G20SPIRTRU  G20SPIDMAN  \
0        2304         561        2293         573        2301         558   
1        2381         537        2362         563        2361         551   
2        1999         561        1981         575        1962         593   
3          73         613          72         618          70         617   
4         461        1225         447        1232         467        1216   

   G20SSCRNEW  G20SSCDBEA  G20SSCRBER  G20SSCDINM  G20SSCRBAR  G20SSCDDAV  \
0        2239         630        2275         588        2259         596   
1        2306         625        2359         568        2315         601   
2        1923         643        1970         587        1952         603   
3          67         619          76         612          80         604   
4         441        1245         449        1234         469        1216   

   G20SACRWOO  G20SACDSHI  G20SACRGOR  G20SACDCUB  G20SACRDIL  G20SACDSTY  \
0        2290         566        2276         571        2296         548   
1        2354         558        2347         562        2367         534   
2        1967         578        1945         596        1977         570   
3          81         607          76         612          74         614   
4         461        1212         452        1227         465        1209   

   G20SACRCAR  G20SACDYOU  G20SACRGRI  G20SACDBRO  \
0        2280         567        2274         568   
1        2349         555        2359         543   
2        1963         579        1954         585   
3          77         602          76         602   
4         454        1224         456        1220   

               

In [37]:
sldu_order = [i for i in sldu_vest.columns]
sldu_order.remove('geometry')
sldu_order.remove('UNIQUE_ID')
sldu_order.remove('COUNTYFP')
sldu_order.append('geometry')
sldu_order.remove('SLDU_DIST')
sldu_order[4:4] = ['SLDU_DIST']
sldu_order[0:1] = ['UNIQUE_ID','COUNTYFP']

In [38]:
sldu_vest_df = sldu_vest[sldu_order]
for i in sldu_vest_df.columns:
    if i.startswith('G'):
        sldu_vest_df[i] = sldu_vest_df[i].astype(int)
    elif i!='geometry':
        sldu_vest_df[i] = sldu_vest_df[i].astype(str)
    else:
        continue
sldu_vest_df.head()

C:\Users\SpencerNelson\Anaconda3\envs\rdh\lib\site-packages\geopandas\geodataframe.py:1322: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super(GeoDataFrame, self).__setitem__(key, value)


UNIQUE_ID COUNTYFP   ENR_DESC   COUNTY_NAM COUNTY_ID SLDU_DIST  \
0      01_ALAMANCE      001  PATTERSON     ALAMANCE         1        24   
1      02_ALAMANCE      001      COBLE     ALAMANCE         1        24   
2      07_ALAMANCE      001   ALBRIGHT     ALAMANCE         1        24   
3     H08_GUILFORD      041        H08     GUILFORD        41        26   
4  079_MECKLENBURG      060        079  MECKLENBURG        60        38   

   G20PRERTRU  G20PREDBID  G20PRELJOR  G20PREGHAW  G20PRECBLA  G20PREOWRI  \
0        2299         566          27           6           5           4   
1        2387         559          15           4           4           3   
2        1996         581          20           9           1           4   
3          73         614           3           1           2           2   
4         469        1223           8           9           2           6   

   G20USSRTIL  G20USSDCUN  G20USSLBRA  G20USSCHAY  G20GOVRFOR  G20GOVDCOO  \
0        2205         564          68          51        2209         661   
1        2290         570          65          32        2264         677   
2        1917         588          63          23        1936         644   
3          70         595          11          12          63         621   
4         418        1190          64          29         418        1250   

   G20GOVLDIF  G20GOVCPIS  G20LTGRROB  G20LTGDHOL  G20ATGRONE  G20ATGDSTE  \
0          19          13        2336         556        2266         618   
1          18           9        2391         556        2323         614   
2          19           3        2013         578        1957         616   
3           3           6          76         615          79         611   
4          33          17         460        1232         443        1244   

   G20TRERFOL  G20TREDCHA  G20SOSRSYK  G20SOSDMAR  G20AUDRSTR  G20AUDDWOO  \
0        2240         611        2251         617        2247         608   
1        2319         603        2270         663        2301         612   
2        1968         595        1903         659        1927         629   
3          89         598          67         617          77         610   
4         495        1182         427        1259         443        1236   

   G20AGRRTRO  G20AGRDWAD  G20INSRCAU  G20INSDGOO  G20LABRDOB  G20LABDHOL  \
0        2401         485        2304         561        2293         573   
1        2468         472        2381         537        2362         563   
2        2078         502        1999         561        1981         575   
3          76         613          73         613          72         618   
4         454        1230         461        1225         447        1232   

   G20SPIRTRU  G20SPIDMAN  G20SSCRNEW  G20SSCDBEA  G20SSCRBER  G20SSCDINM  \
0        2301         558        2239         630        2275         588   
1        2361         551        2306         625        2359         568   
2        1962         593        1923         643        1970         587   
3          70         617          67         619          76         612   
4         467        1216         441        1245         449        1234   

   G20SSCRBAR  G20SSCDDAV  G20SACRWOO  G20SACDSHI  G20SACRGOR  G20SACDCUB  \
0        2259         596        2290         566        2276         571   
1        2315         601        2354         558        2347         562   
2        1952         603        1967         578        1945         596   
3          80         604          81         607          76         612   
4         469        1216         461        1212         452        1227   

   G20SACRDIL  G20SACDSTY  G20SACRCAR  G20SACDYOU  G20SACRGRI  G20SACDBRO  \
0        2296         548        2280         567        2274         568   
1        2367         534        2349         555        2359         543   
2        1977         570        1963         579        1954         585   
3        

In [39]:
sldu_vest_df.to_file('./nc_gen_20_st_sldu_prec.shp')

## Process Congressional dataframe

In [40]:
districts = os.path.join(source_files, 'district_bounds')
congress_folder = os.path.join(districts,'congress')
congress_shp = gp.read_file(os.path.join(congress_folder,'C-Goodwin-A-1-TC.shp'))
congress_shp.head()

DISTRICT  POPULATION                                           geometry
0       12      733499  POLYGON ((449362.059 184483.802, 449368.426 18...
1        2      733499  POLYGON ((622633.549 201431.242, 622384.873 20...
2        3      733499  POLYGON ((773148.847 217156.853, 773146.315 21...
3        1      733498  POLYGON ((747975.917 187057.151, 747789.630 18...
4        4      733499  POLYGON ((570678.318 223963.120, 570684.661 22...

In [41]:
congress_shp['DISTRICT'] = congress_shp['DISTRICT'].apply(lambda x: x.zfill(2))
congress_shp.head()

DISTRICT  POPULATION                                           geometry
0       12      733499  POLYGON ((449362.059 184483.802, 449368.426 18...
1       02      733499  POLYGON ((622633.549 201431.242, 622384.873 20...
2       03      733499  POLYGON ((773148.847 217156.853, 773146.315 21...
3       01      733498  POLYGON ((747975.917 187057.151, 747789.630 18...
4       04      733499  POLYGON ((570678.318 223963.120, 570684.661 22...

In [42]:
cong_precs_split_list = list(cong_split_dictionary.keys())
cong_precs_split = cong_df[cong_df['PREC_CO'].isin(cong_precs_split_list)].copy()
cong_df_dropped  = cong_df[~cong_df['PREC_CO'].isin(cong_precs_split_list)].copy()
display(cong_precs_split)
print(len(cong_precs_split))

PIVOT_COL          PREC_CO  GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  \
451              0601_PITT         0.0         1.0         0.0         0.0   
455            062_FORSYTH         0.0         0.0         0.0         0.0   
610        096_MECKLENBURG         0.0         0.0         0.0         0.0   
638             10-03_WAKE         0.0         0.0      1358.0        52.0   
694             1102A_PITT       662.0       926.0         0.0         0.0   
1102       217_MECKLENBURG         0.0         0.0         0.0         0.0   
1103       218_MECKLENBURG         0.0         0.0         0.0         0.0   
1179            26_CATAWBA         0.0         0.0         0.0         0.0   
1205            29_CATAWBA         0.0         0.0         0.0         0.0   
1228            30_CATAWBA         0.0         0.0         0.0         0.0   
1234         30_RUTHERFORD         0.0         0.0         0.0         0.0   
1280            37_CATAWBA         0.0         0.0         0.0         0.0   
1622                C2_LEE         0.0         0.0         0.0         0.0   
1661           CC3_IREDELL         0.0         0.0         0.0         0.0   
1806        ESC114_CHATHAM         0.0         0.0         0.0         0.0   
1809          EUR-WP_MOORE         0.0         0.0         0.0         0.0   
1811             EWD_MOORE         0.0         0.0         0.0         0.0   
2110            KITT_VANCE       974.0      1164.0         0.0         0.0   
2648          PR32_HARNETT         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON02RSWA  GCON03DFAR  GCON03RMUR  GCON04DPRI  GCON04RTHO  \
451               0.0       942.0      3074.0         0.0         0.0   
455               0.0         0.0         0.0         0.0         0.0   
610               0.0         0.0         0.0         0.0         0.0   
638             926.0         0.0         0.0        13.0        24.0   
694               0.0       431.0       707.0         0.0         0.0   
1102              0.0         0.0         0.0         0.0         0.0   
1103              0.0         0.0         0.0         0.0         0.0   
1179              0.0         0.0         0.0         0.0         0.0   
1205              0.0         0.0         0.0         0.0         0.0   
1228              0.0         0.0         0.0         0.0         0.0   
1234              0.0         0.0         0.0         0.0         0.0   
1280              0.0         0.0         0.0         0.0         0.0   
1622              0.0         0.0         0.0         0.0         0.0   
1661              0.0         0.0         0.0         0.0         0.0   
1806              0.0         0.0         0.0       723.0       842.0   
1809              0.0         0.0         0.0         0.0         0.0   
1811              0.0         0.0         0.0         0.0         0.0   
2110              0.0         0.0         0.0       262.0       358.0   
2648              0.0         0.0         0.0         0.0         0.0   

PIVOT_COL  GCON05CGRE  GCON05DBRO  GCON05RFOX  GCON06DMAN  GCON06RHAY  \
451               0.0         0.0         0.0         0.0         0.0   
455               0.0         0.0         0.0        90.0        96.0   
610               0.0         0.0         0.0         0.0         0.0   
638               0.0         0.0         0.0         0.0         0.0   
694               0.0         0.0         0.0         0.0         0.0   
1102              0.0         0.0         0.0         0.0         0.0   
1103              0.0         0.0         0.0         0.0         0.0   
1179             18.0       634.0       879.0         0.0         0.0   
1205             28.0       508.0      1519.0         0.0         0.0   
1228              0.0        20.0        39.0         0.0         0.0   
1234             34.0       609.0      1024.0         0.0         0.0   
1280              2.0        37.0        58.0         0.0         0.0   
1622              0.0        

19


In [43]:
print(len(cong_unsplit_dict))
print(len(cong_df_dropped))
cong_df_dropped['CONG_DIST'] = cong_df_dropped['PREC_CO'].apply(lambda x: cong_unsplit_dict.get(x))
vest_sub = vest[['PREC_ID','ENR_DESC','COUNTY_NAM','COUNTY_ID','MATCH','geometry']]
cong_df_dropped = pd.merge(vest_sub,cong_df_dropped,on='MATCH')
cong_df_dropped.head()

2643
2643


PREC_ID   ENR_DESC   COUNTY_NAM COUNTY_ID            MATCH  \
0      01  PATTERSON     ALAMANCE         1      01_ALAMANCE   
1      02      COBLE     ALAMANCE         1      02_ALAMANCE   
2      07   ALBRIGHT     ALAMANCE         1      07_ALAMANCE   
3     H08        H08     GUILFORD        41     H08_GUILFORD   
4     079        079  MECKLENBURG        60  079_MECKLENBURG   

                                            geometry          PREC_CO  \
0  POLYGON ((1839239.963 762333.301, 1839240.297 ...      01_ALAMANCE   
1  POLYGON ((1840088.847 807206.254, 1840090.437 ...      02_ALAMANCE   
2  POLYGON ((1871943.040 801230.531, 1871943.510 ...      07_ALAMANCE   
3  POLYGON ((1702354.926 805008.445, 1702627.359 ...     H08_GUILFORD   
4  POLYGON ((1410451.445 548338.307, 1410462.273 ...  079_MECKLENBURG   

   GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  GCON02RSWA  GCON03DFAR  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON03RMUR  GCON04DPRI  GCON04RTHO  GCON05CGRE  GCON05DBRO  GCON05RFOX  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON06DMAN  GCON06RHAY  GCON07DWAR  GCON07OWRI  GCON07RROU  GCON08DTIM  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3       606.0        74.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON08RHUD  GCON09DWAL  GCON09RBIS  GCON10DPAR  GCON10RMCH  GCON11DDAV  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  GCON13DHUF  GCON13RBUD  \
0         0.0         0.0         0.0         0.0       551.0      2327.0   
1         0.0         0.0         0.0         0.0       555.0      2380.0   
2         0.0         0.0         0.0         0.0       567.0      2004.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0      1363.0         0.0         0.0   

  PRECINCT       COUNTY CONG_DIST  
0       01     ALAMANCE        13  
1       02     ALAMANCE        13  
2       07     ALAMANCE        13  
3      H08     GUILFORD        06  
4      079  MECKLENBURG        12

In [44]:
print(len(cong_precs_split))
print(len(cong_split_dictionary))
cong_precs_split_expanded_list = []
for k,v in cong_split_dictionary.items():
    sub_dfs = []
    len_splits = len(v)
    for i in range(0,len_splits):
        dist = v[i]
        sub = cong_precs_split[cong_precs_split['PREC_CO']==k]
        sub['CONG_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
        sub['CONG_DIST'] = sub['CONG_DIST'].astype(str)
        sub['CONG_DIST_long'] = sub['CONG_DIST'].apply(lambda x: ''.join([(' '.join(['[CD-',x])),']']))
        sub['UNIQUE_ID'] = sub.apply(lambda x: ' '.join([x['PREC_CO'],x['CONG_DIST_long']]),axis=1)
        to_keep = []
        for col in sub.columns:
            if col.startswith('GCON'):
                if str(dist) in str(col):
                    to_keep.append(col)
                else:
                    continue
            else:
                to_keep.append(col)
        sub = sub[to_keep]
        sub_dfs.append(sub)
    new_df = pd.concat(sub_dfs)
    cong_precs_split_expanded_list.append(new_df)
cong_precs_split_expanded = pd.concat(cong_precs_split_expanded_list)
cong_precs_split_expanded = cong_precs_split_expanded.fillna(0)
cong_precs_split_expanded_cols = list(cong_precs_split_expanded.columns)
display(cong_precs_split_expanded)

19
19


<ipython-input-44-c2e23502f588>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['CONG_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
<ipython-input-44-c2e23502f588>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['CONG_DIST'] = sub['CONG_DIST'].astype(str)
<ipython-input-44-c2e23502f588>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata

PIVOT_COL          PREC_CO  GCON01DBUT  GCON01RSMI PRECINCT       COUNTY  \
451              0601_PITT         0.0         1.0     0601         PITT   
451              0601_PITT         0.0         0.0     0601         PITT   
455            062_FORSYTH         0.0         0.0      062      FORSYTH   
455            062_FORSYTH         0.0         0.0      062      FORSYTH   
610        096_MECKLENBURG         0.0         0.0      096  MECKLENBURG   
610        096_MECKLENBURG         0.0         0.0      096  MECKLENBURG   
638             10-03_WAKE         0.0         0.0    10-03         WAKE   
638             10-03_WAKE         0.0         0.0    10-03         WAKE   
694             1102A_PITT       662.0       926.0    1102A         PITT   
694             1102A_PITT         0.0         0.0    1102A         PITT   
1102       217_MECKLENBURG         0.0         0.0      217  MECKLENBURG   
1102       217_MECKLENBURG         0.0         0.0      217  MECKLENBURG   
1103       218_MECKLENBURG         0.0         0.0      218  MECKLENBURG   
1103       218_MECKLENBURG         0.0         0.0      218  MECKLENBURG   
1179            26_CATAWBA         0.0         0.0       26      CATAWBA   
1179            26_CATAWBA         0.0         0.0       26      CATAWBA   
1205            29_CATAWBA         0.0         0.0       29      CATAWBA   
1205            29_CATAWBA         0.0         0.0       29      CATAWBA   
1228            30_CATAWBA         0.0         0.0       30      CATAWBA   
1228            30_CATAWBA         0.0         0.0       30      CATAWBA   
1234         30_RUTHERFORD         0.0         0.0       30   RUTHERFORD   
1234         30_RUTHERFORD         0.0         0.0       30   RUTHERFORD   
1280            37_CATAWBA         0.0         0.0       37      CATAWBA   
1280            37_CATAWBA         0.0         0.0       37      CATAWBA   
1622                C2_LEE         0.0         0.0       C2          LEE   
1622                C2_LEE         0.0         0.0       C2          LEE   
1661           CC3_IREDELL         0.0         0.0      CC3      IREDELL   
1661           CC3_IREDELL         0.0         0.0      CC3      IREDELL   
1806        ESC114_CHATHAM         0.0         0.0   ESC114      CHATHAM   
1806        ESC114_CHATHAM         0.0         0.0   ESC114      CHATHAM   
1809          EUR-WP_MOORE         0.0         0.0   EUR-WP        MOORE   
1809          EUR-WP_MOORE         0.0         0.0   EUR-WP        MOORE   
1811             EWD_MOORE         0.0         0.0      EWD        MOORE   
1811             EWD_MOORE         0.0         0.0      EWD        MOORE   
2110            KITT_VANCE       974.0      1164.0     KITT        VANCE   
2110            KITT_VANCE         0.0         0.0     KITT        VANCE   
2648          PR32_HARNETT         0.0         0.0     PR32      HARNETT   
2648          PR32_HARNETT         0.0         0.0     PR32      HARNETT   

PIVOT_COL            MATCH CONG_DIST CONG_DIST_long                 UNIQUE_ID  \
451              0601_PITT        01       [CD- 01]        0601_PITT [CD- 01]   
451              0601_PITT        03       [CD- 03]        0601_PITT [CD- 03]   
455            062_FORSYTH        06       [CD- 06]      062_FORSYTH [CD- 06]   
455            062_FORSYTH        10       [CD- 10]      062_FORSYTH [CD- 10]   
610        096_MECKLENBURG        09       [CD- 09]  096_MECKLENBURG [CD- 09]   
610        096_MECKLENBURG        12       [CD- 12]  096_MECKLENBURG [CD- 12]   
638             10-03_WAKE        02       [CD- 02]       10-03_WAKE [CD- 02]   
638             10-03_WAKE        04       [CD- 04]       10-03_WAKE [CD- 04]   
694             1102A_PITT        01       [CD- 01]       1102A_PITT [CD- 01]   
694             1102A_PITT        03       [CD- 03]       1102A_PITT [CD- 03]   
1102       217_MECKLENBURG        09       [CD- 09]  217_MECKLENBURG [CD- 09]   
1102       217_MECKLENBURG        12       [CD- 12]  217_MECKLE

In [45]:
def make_district_dict(district_shp,district_field):
    keys = []
    values = []
    for i in district_shp[district_field]:
        dist = district_shp[district_shp[district_field]==i].copy()
        dist = dist[[district_field,'geometry']]
        keys.append(i)
        values.append(dist)
    dictionary = dict(zip(keys,values))
    return dictionary

In [46]:
cong_dict = make_district_dict(congress_shp,'DISTRICT')

In [47]:
new_precs = []
for k,v in cong_split_dictionary.items():
    original_geom = vest[vest['MATCH']==k]['geometry']
    original_geom = gp.GeoDataFrame(original_geom)
    original_geom_crs = original_geom.crs
    dists = []
    for i in v:
        dist_of_interest = cong_dict.get(i)
        dists.append(dist_of_interest)
    for i in dists:
        dist_of_interest_geom = i#['geometry']
        district = i['DISTRICT'].unique()[0]
        #print('Current district to split by: ', district)
        dist_of_interest_geom =dist_of_interest_geom.to_crs(original_geom_crs) 
        new_prec = gp.overlay(original_geom, dist_of_interest_geom, how='intersection',keep_geom_type=False)
        new_prec['UNIQUE_ID'] = str(k + ' [CD- '+str(district)+ ']')
        new_precs.append(new_prec)
new_precs = pd.concat(new_precs)
display(new_precs)

cong_precs_split_newgeom = pd.merge(cong_precs_split_expanded,new_precs,on='UNIQUE_ID',how='outer',indicator=True)
cong_precs_split_newgeom['CONG_DIST'] = cong_precs_split_newgeom['DISTRICT']
cong_precs_split_newgeom.drop(columns= ['_merge','DISTRICT'],inplace=True)
display(cong_precs_split_newgeom)

DISTRICT                                           geometry  \
0       01  MULTIPOLYGON (((2520528.389 654716.473, 252053...   
0       03  POLYGON ((2491908.291 641579.518, 2492018.791 ...   
0       06  MULTIPOLYGON (((1683652.730 871179.386, 168365...   
0       10  POLYGON ((1678269.341 882696.661, 1678269.341 ...   
0       09  MULTIPOLYGON (((1479211.904 506326.020, 147924...   
0       12  POLYGON ((1473340.274 508030.500, 1473414.202 ...   
0       02  POLYGON ((2177270.975 747380.167, 2177295.876 ...   
0       04  MULTIPOLYGON (((2198280.732 741411.673, 219828...   
0       01  POLYGON ((2501356.768 670518.581, 2501356.768 ...   
0       03  MULTIPOLYGON (((2507570.670 660738.615, 250746...   
0       09  MULTIPOLYGON (((1492269.646 502564.649, 149219...   
0       12  MULTIPOLYGON (((1479211.904 506326.020, 147921...   
0       09  POLYGON ((1505410.320 504556.924, 1505374.096 ...   
0       12  POLYGON ((1492395.014 502602.907, 1492637.838 ...   
0       10  POLYGON ((1295947.154 738231.949, 1295947.235 ...   
0       05  MULTIPOLYGON (((1295947.235 738232.075, 129604...   
0       10  MULTIPOLYGON (((1339435.371 757291.180, 133903...   
0       05  POLYGON ((1319649.509 747016.190, 1319612.908 ...   
0       10  POLYGON ((1315569.649 739338.159, 1315633.264 ...   
0       05  MULTIPOLYGON (((1326766.547 740748.257, 132676...   
0       11  MULTIPOLYGON (((1123012.341 601074.541, 112301...   
0       05  MULTIPOLYGON (((1133600.789 605222.319, 113360...   
0       10  POLYGON ((1308014.364 740739.924, 1308014.364 ...   
0       05  MULTIPOLYGON (((1308017.182 741465.858, 130801...   
0       08  POLYGON ((1935600.977 615677.021, 1935667.682 ...   
0       13  MULTIPOLYGON (((1907666.910 611187.352, 190790...   
0       13  POLYGON ((1472354.182 683722.657, 1472375.596 ...   
0       10  MULTIPOLYGON (((1459394.281 670365.799, 145991...   
0       13  MULTIPOLYGON (((1846688.696 735723.589, 184675...   
0       04  POLYGON ((1889708.572 734234.126, 1889708.572 ...   
0       09  MULTIPOLYGON (((1894524.752 543573.303, 189425...   
0       08  POLYGON ((1898208.617 546101.872, 1898177.530 ...   
0       09  POLYGON ((1875477.241 557837.988, 1875438.799 ...   
0       08  MULTIPOLYGON (((1875410.930 554701.372, 187541...   
0       01  MULTIPOLYGON (((2150616.406 903797.329, 215061...   
0       04  MULTIPOLYGON (((2189728.362 905006.175, 218973...   
0       08  MULTIPOLYGON (((2052013.949 612439.965, 205219...   
0       07  MULTIPOLYGON (((2074320.125 625006.437, 207432...   

                  UNIQUE_ID  
0        0601_PITT [CD- 01]  
0        0601_PITT [CD- 03]  
0      062_FORSYTH [CD- 06]  
0      062_FORSYTH [CD- 10]  
0  096_MECKLENBURG [CD- 09]  
0  096_MECKLENBURG [CD- 12]  
0       10-03_WAKE [CD- 02]  
0       10-03_WAKE [CD- 04]  
0       1102A_PITT [CD- 01]  
0       1102A_PITT [CD- 03]  
0  217_MECKLENBURG [CD- 09]  
0  217_MECKLENBURG [CD- 12]  
0  218_MECKLENBURG [CD- 09]  
0  218_MECKLENBURG [CD- 12]  
0       26_CATAWBA [CD- 10]  
0       26_CATAWBA [CD- 05]  
0       29_CATAWBA [CD- 10]  
0       29_CATAWBA [CD- 05]  
0       30_CATAWBA [CD- 10]  
0       30_CATAWBA [CD- 05]  
0    30_RUTHERFORD [CD- 11]  
0    30_RUTHERFORD [CD- 05]  
0       37_CATAWBA [CD- 10]  
0       37_CATAWBA [CD- 05]  
0           C2_LEE [CD- 08]  
0           C2_LEE [CD- 13]  
0      CC3_IREDELL [CD- 13]  
0      CC3_IREDELL [CD- 10]  
0   ESC114_CHATHAM [CD- 13]  
0   ESC114_CHATHAM [CD- 04]  
0     EUR-WP_MOORE [CD- 09]  
0     EUR-WP_MOORE [CD- 08]  
0        EWD_MOORE [CD- 09]  
0        EWD_MOORE [CD- 08]  
0       KITT_VANCE [CD- 01]  
0       KITT_VANCE [CD- 04]  
0     PR32_HARNETT [CD- 08]  
0     PR32_HARNETT [CD- 07]

PREC_CO  GCON01DBUT  GCON01RSMI PRECINCT       COUNTY  \
0         0601_PITT         0.0         1.0     0601         PITT   
1         0601_PITT         0.0         0.0     0601         PITT   
2       062_FORSYTH         0.0         0.0      062      FORSYTH   
3       062_FORSYTH         0.0         0.0      062      FORSYTH   
4   096_MECKLENBURG         0.0         0.0      096  MECKLENBURG   
5   096_MECKLENBURG         0.0         0.0      096  MECKLENBURG   
6        10-03_WAKE         0.0         0.0    10-03         WAKE   
7        10-03_WAKE         0.0         0.0    10-03         WAKE   
8        1102A_PITT       662.0       926.0    1102A         PITT   
9        1102A_PITT         0.0         0.0    1102A         PITT   
10  217_MECKLENBURG         0.0         0.0      217  MECKLENBURG   
11  217_MECKLENBURG         0.0         0.0      217  MECKLENBURG   
12  218_MECKLENBURG         0.0         0.0      218  MECKLENBURG   
13  218_MECKLENBURG         0.0         0.0      218  MECKLENBURG   
14       26_CATAWBA         0.0         0.0       26      CATAWBA   
15       26_CATAWBA         0.0         0.0       26      CATAWBA   
16       29_CATAWBA         0.0         0.0       29      CATAWBA   
17       29_CATAWBA         0.0         0.0       29      CATAWBA   
18       30_CATAWBA         0.0         0.0       30      CATAWBA   
19       30_CATAWBA         0.0         0.0       30      CATAWBA   
20    30_RUTHERFORD         0.0         0.0       30   RUTHERFORD   
21    30_RUTHERFORD         0.0         0.0       30   RUTHERFORD   
22       37_CATAWBA         0.0         0.0       37      CATAWBA   
23       37_CATAWBA         0.0         0.0       37      CATAWBA   
24           C2_LEE         0.0         0.0       C2          LEE   
25           C2_LEE         0.0         0.0       C2          LEE   
26      CC3_IREDELL         0.0         0.0      CC3      IREDELL   
27      CC3_IREDELL         0.0         0.0      CC3      IREDELL   
28   ESC114_CHATHAM         0.0         0.0   ESC114      CHATHAM   
29   ESC114_CHATHAM         0.0         0.0   ESC114      CHATHAM   
30     EUR-WP_MOORE         0.0         0.0   EUR-WP        MOORE   
31     EUR-WP_MOORE         0.0         0.0   EUR-WP        MOORE   
32        EWD_MOORE         0.0         0.0      EWD        MOORE   
33        EWD_MOORE         0.0         0.0      EWD        MOORE   
34       KITT_VANCE       974.0      1164.0     KITT        VANCE   
35       KITT_VANCE         0.0         0.0     KITT        VANCE   
36     PR32_HARNETT         0.0         0.0     PR32      HARNETT   
37     PR32_HARNETT         0.0         0.0     PR32      HARNETT   

              MATCH CONG_DIST CONG_DIST_long                 UNIQUE_ID  \
0         0601_PITT        01       [CD- 01]        0601_PITT [CD- 01]   
1         0601_PITT        03       [CD- 03]        0601_PITT [CD- 03]   
2       062_FORSYTH        06       [CD- 06]      062_FORSYTH [CD- 06]   
3       062_FORSYTH        10       [CD- 10]      062_FORSYTH [CD- 10]   
4   096_MECKLENBURG        09       [CD- 09]  096_MECKLENBURG [CD- 09]   
5   096_MECKLENBURG        12       [CD- 12]  096_MECKLENBURG [CD- 12]   
6        10-03_WAKE        02       [CD- 02]       10-03_WAKE [CD- 02]   
7        10-03_WAKE        04       [CD- 04]       10-03_WAKE [CD- 04]   
8        1102A_PITT        01       [CD- 01]       1102A_PITT [CD- 01]   
9        1102A_PITT        03       [CD- 03]       1102A_PITT [CD- 03]   
10  217_MECKLENBURG        09       [CD- 09]  217_MECKLENBURG [CD- 09]   
11  217_MECKLENBURG        12       [CD- 12]  217_MECKLENBURG [CD- 12]   
12  218_MECKLENBURG        09       [CD- 09]  218_MECKLENBURG [CD- 09]   
13  218_MECKLENBURG        12       [CD- 12]  218_MECKLENBURG [CD- 12]   
14       26_CATAWBA        10       [CD- 10]       26_CATAWBA [CD- 10]   
15       26_CATAWBA        05       [CD- 05]       26_CATAWBA [CD- 05]   
16       29_CATAWBA        10       [CD- 10]       29_CATAWBA 

In [48]:
vest_sub_split_join = vest_sub.drop(columns = ['geometry'])
vest_sub_split_join = pd.DataFrame(vest_sub_split_join)
cong_precs_split_newgeom = pd.merge(cong_precs_split_newgeom,vest_sub_split_join,on='MATCH', how = 'outer',indicator = True)
cong_precs_split_newgeom = cong_precs_split_newgeom[cong_precs_split_newgeom['_merge']=='both']
display(cong_precs_split_newgeom)

PREC_CO  GCON01DBUT  GCON01RSMI PRECINCT       COUNTY  \
0         0601_PITT         0.0         1.0     0601         PITT   
1         0601_PITT         0.0         0.0     0601         PITT   
2       062_FORSYTH         0.0         0.0      062      FORSYTH   
3       062_FORSYTH         0.0         0.0      062      FORSYTH   
4   096_MECKLENBURG         0.0         0.0      096  MECKLENBURG   
5   096_MECKLENBURG         0.0         0.0      096  MECKLENBURG   
6        10-03_WAKE         0.0         0.0    10-03         WAKE   
7        10-03_WAKE         0.0         0.0    10-03         WAKE   
8        1102A_PITT       662.0       926.0    1102A         PITT   
9        1102A_PITT         0.0         0.0    1102A         PITT   
10  217_MECKLENBURG         0.0         0.0      217  MECKLENBURG   
11  217_MECKLENBURG         0.0         0.0      217  MECKLENBURG   
12  218_MECKLENBURG         0.0         0.0      218  MECKLENBURG   
13  218_MECKLENBURG         0.0         0.0      218  MECKLENBURG   
14       26_CATAWBA         0.0         0.0       26      CATAWBA   
15       26_CATAWBA         0.0         0.0       26      CATAWBA   
16       29_CATAWBA         0.0         0.0       29      CATAWBA   
17       29_CATAWBA         0.0         0.0       29      CATAWBA   
18       30_CATAWBA         0.0         0.0       30      CATAWBA   
19       30_CATAWBA         0.0         0.0       30      CATAWBA   
20    30_RUTHERFORD         0.0         0.0       30   RUTHERFORD   
21    30_RUTHERFORD         0.0         0.0       30   RUTHERFORD   
22       37_CATAWBA         0.0         0.0       37      CATAWBA   
23       37_CATAWBA         0.0         0.0       37      CATAWBA   
24           C2_LEE         0.0         0.0       C2          LEE   
25           C2_LEE         0.0         0.0       C2          LEE   
26      CC3_IREDELL         0.0         0.0      CC3      IREDELL   
27      CC3_IREDELL         0.0         0.0      CC3      IREDELL   
28   ESC114_CHATHAM         0.0         0.0   ESC114      CHATHAM   
29   ESC114_CHATHAM         0.0         0.0   ESC114      CHATHAM   
30     EUR-WP_MOORE         0.0         0.0   EUR-WP        MOORE   
31     EUR-WP_MOORE         0.0         0.0   EUR-WP        MOORE   
32        EWD_MOORE         0.0         0.0      EWD        MOORE   
33        EWD_MOORE         0.0         0.0      EWD        MOORE   
34       KITT_VANCE       974.0      1164.0     KITT        VANCE   
35       KITT_VANCE         0.0         0.0     KITT        VANCE   
36     PR32_HARNETT         0.0         0.0     PR32      HARNETT   
37     PR32_HARNETT         0.0         0.0     PR32      HARNETT   

              MATCH CONG_DIST CONG_DIST_long                 UNIQUE_ID  \
0         0601_PITT        01       [CD- 01]        0601_PITT [CD- 01]   
1         0601_PITT        03       [CD- 03]        0601_PITT [CD- 03]   
2       062_FORSYTH        06       [CD- 06]      062_FORSYTH [CD- 06]   
3       062_FORSYTH        10       [CD- 10]      062_FORSYTH [CD- 10]   
4   096_MECKLENBURG        09       [CD- 09]  096_MECKLENBURG [CD- 09]   
5   096_MECKLENBURG        12       [CD- 12]  096_MECKLENBURG [CD- 12]   
6        10-03_WAKE        02       [CD- 02]       10-03_WAKE [CD- 02]   
7        10-03_WAKE        04       [CD- 04]       10-03_WAKE [CD- 04]   
8        1102A_PITT        01       [CD- 01]       1102A_PITT [CD- 01]   
9        1102A_PITT        03       [CD- 03]       1102A_PITT [CD- 03]   
10  217_MECKLENBURG        09       [CD- 09]  217_MECKLENBURG [CD- 09]   
11  217_MECKLENBURG        12       [CD- 12]  217_MECKLENBURG [CD- 12]   
12  218_MECKLENBURG        09       [CD- 09]  218_MECKLENBURG [CD- 09]   
13  218_MECKLENBURG        12       [CD- 12]  218_MECKLENBURG [CD- 12]   
14       26_CATAWBA        10       [CD- 10]       26_CATAWBA [CD- 10]   
15       26_CATAWBA        05       [CD- 05]       26_CATAWBA [CD- 05]   
16       29_CATAWBA        10       [CD- 10]       29_CATAWBA 

In [49]:
##CONCAT THE DFS
cong_final_df = pd.concat([cong_df_dropped,cong_precs_split_newgeom])
cong_final_df['UNIQUE_ID'] = cong_final_df['UNIQUE_ID'].astype(str)
cong_final_df.head()

PREC_ID   ENR_DESC   COUNTY_NAM COUNTY_ID            MATCH  \
0      01  PATTERSON     ALAMANCE         1      01_ALAMANCE   
1      02      COBLE     ALAMANCE         1      02_ALAMANCE   
2      07   ALBRIGHT     ALAMANCE         1      07_ALAMANCE   
3     H08        H08     GUILFORD        41     H08_GUILFORD   
4     079        079  MECKLENBURG        60  079_MECKLENBURG   

                                            geometry          PREC_CO  \
0  POLYGON ((1839239.963 762333.301, 1839240.297 ...      01_ALAMANCE   
1  POLYGON ((1840088.847 807206.254, 1840090.437 ...      02_ALAMANCE   
2  POLYGON ((1871943.040 801230.531, 1871943.510 ...      07_ALAMANCE   
3  POLYGON ((1702354.926 805008.445, 1702627.359 ...     H08_GUILFORD   
4  POLYGON ((1410451.445 548338.307, 1410462.273 ...  079_MECKLENBURG   

   GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  GCON02RSWA  GCON03DFAR  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON03RMUR  GCON04DPRI  GCON04RTHO  GCON05CGRE  GCON05DBRO  GCON05RFOX  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON06DMAN  GCON06RHAY  GCON07DWAR  GCON07OWRI  GCON07RROU  GCON08DTIM  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3       606.0        74.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON08RHUD  GCON09DWAL  GCON09RBIS  GCON10DPAR  GCON10RMCH  GCON11DDAV  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  GCON13DHUF  GCON13RBUD  \
0         0.0         0.0         0.0         0.0       551.0      2327.0   
1         0.0         0.0         0.0         0.0       555.0      2380.0   
2         0.0         0.0         0.0         0.0       567.0      2004.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0      1363.0         0.0         0.0   

  PRECINCT       COUNTY CONG_DIST CONG_DIST_long UNIQUE_ID _merge  
0       01     ALAMANCE        13            NaN       nan    NaN  
1       02     ALAMANCE        13            NaN       nan    NaN  
2       07     ALAMANCE        13            NaN       nan    NaN  
3      H08     GUILFORD        06            NaN       nan    NaN  
4      079  MECKLENBURG        12            NaN       nan    NaN

In [50]:
cong_final_df['COUNTY_ID'] = cong_final_df['COUNTY_ID'].astype(str)
cong_final_df['COUNTYFP'] = cong_final_df['COUNTY_ID'].apply(lambda x: str(x).zfill(3))
#cong_final_df = cong_final_df.fillna(0) 
cong_final_df['UNIQUE_ID'] = cong_final_df.apply(lambda x: x['MATCH'] if x['UNIQUE_ID']=='nan' else x['UNIQUE_ID'],axis=1)
cong_final_df.drop(columns = ['PREC_CO','MATCH','PRECINCT','COUNTY','CONG_DIST_long','_merge'],inplace=True)
cong_final_df_cols = list(cong_final_df.columns)
cong_final_df_cols.remove('geometry')
cong_final_df_cols.remove('CONG_DIST')
cong_final_df_cols.remove('UNIQUE_ID')
cong_final_df_cols.remove('COUNTYFP')
cong_final_df_cols[0:1] = ['UNIQUE_ID','COUNTYFP']
cong_final_df_cols[5:5] = ['CONG_DIST']
cong_final_df_cols.append('geometry')
cong_final_df = cong_final_df[cong_final_df_cols]

for i in cong_final_df.columns:
    if i.startswith('G'):
        cong_final_df[i] = cong_final_df[i].astype(int)
    elif i!='geometry':
        cong_final_df[i]= cong_final_df[i].astype(str)
    else:
        continue
display(cong_final_df.head())
display(cong_final_df.tail())

UNIQUE_ID COUNTYFP   ENR_DESC   COUNTY_NAM COUNTY_ID CONG_DIST  \
0      01_ALAMANCE      001  PATTERSON     ALAMANCE         1        13   
1      02_ALAMANCE      001      COBLE     ALAMANCE         1        13   
2      07_ALAMANCE      001   ALBRIGHT     ALAMANCE         1        13   
3     H08_GUILFORD      041        H08     GUILFORD        41        06   
4  079_MECKLENBURG      060        079  MECKLENBURG        60        12   

   GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  GCON02RSWA  GCON03DFAR  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GCON03RMUR  GCON04DPRI  GCON04RTHO  GCON05CGRE  GCON05DBRO  GCON05RFOX  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GCON06DMAN  GCON06RHAY  GCON07DWAR  GCON07OWRI  GCON07RROU  GCON08DTIM  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3         606          74           0           0           0           0   
4           0           0           0           0           0           0   

   GCON08RHUD  GCON09DWAL  GCON09RBIS  GCON10DPAR  GCON10RMCH  GCON11DDAV  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  GCON13DHUF  GCON13RBUD  \
0           0           0           0           0         551        2327   
1           0           0           0           0         555        2380   
2           0           0           0           0         567        2004   
3           0           0           0           0           0           0   
4           0           0           0        1363           0           0   

                                            geometry  
0  POLYGON ((1839239.963 762333.301, 1839240.297 ...  
1  POLYGON ((1840088.847 807206.254, 1840090.437 ...  
2  POLYGON ((1871943.040 801230.531, 1871943.510 ...  
3  POLYGON ((1702354.926 805008.445, 1702627.359 ...  
4  POLYGON ((1410451.445 548338.307, 1410462.273 ...

UNIQUE_ID COUNTYFP                      ENR_DESC COUNTY_NAM  \
33     EWD_MOORE [CD- 08]      063                      EASTWOOD      MOORE   
34    KITT_VANCE [CD- 01]      091                          KITT      VANCE   
35    KITT_VANCE [CD- 04]      091                          KITT      VANCE   
36  PR32_HARNETT [CD- 08]      043  CENTRAL HARNETT NEILLS CREEK    HARNETT   
37  PR32_HARNETT [CD- 07]      043  CENTRAL HARNETT NEILLS CREEK    HARNETT   

   COUNTY_ID CONG_DIST  GCON01DBUT  GCON01RSMI  GCON02DROS  GCON02LMAT  \
33        63        08           0           0           0           0   
34        91        01         974        1164           0           0   
35        91        04           0           0           0           0   
36        43        08           0           0           0           0   
37        43        07           0           0           0           0   

    GCON02RSWA  GCON03DFAR  GCON03RMUR  GCON04DPRI  GCON04RTHO  GCON05CGRE  \
33           0           0           0           0           0           0   
34           0           0           0           0           0           0   
35           0           0           0         262         358           0   
36           0           0           0           0           0           0   
37           0           0           0           0           0           0   

    GCON05DBRO  GCON05RFOX  GCON06DMAN  GCON06RHAY  GCON07DWAR  GCON07OWRI  \
33           0           0           0           0           0           0   
34           0           0           0           0           0           0   
35           0           0           0           0           0           0   
36           0           0           0           0           0           0   
37           0           0           0           0         600           1   

    GCON07RROU  GCON08DTIM  GCON08RHUD  GCON09DWAL  GCON09RBIS  GCON10DPAR  \
33           0           5           6           0           0           0   
34           0           0           0           0           0           0   
35           0           0           0           0           0           0   
36           0         486         721           0           0           0   
37        1287           0           0           0           0           0   

    GCON10RMCH  GCON11DDAV  GCON11GZWI  GCON11LDEB  GCON11RCAW  GCON12DADA  \
33           0           0           0           0           0           0   
34           0           0           0           0           0           0   
35           0           0           0           0           0           0   
36           0           0           0           0           0           0   
37           0           0           0           0           0           0   

    GCON13DHUF  GCON13RBUD                                           geometry  
33           0           0  MULTIPOLYGON (((1875410.930 554701.372, 187541...  
34           0           0  MULTIPOLYGON (((2150616.406 903797.329, 215061...  
35           0           0  MULTIPOLYGON (((2189728.362 905006.175, 218973...  
36           0           0  MULTIPOLYGON (((2052013.949 612439.965, 205219...  
37           0           0  MULTIPOLYGON (((2074320.125 625006.437, 207432...

In [51]:
congress_shp['CONG_DIST'] = congress_shp['DISTRICT'].astype(str)

In [52]:
cong_final_df.to_file('./nc_gen_20_cong_prec.shp')

### Process House of Representatives dataframe

In [53]:
### READ IN THE HOR FILE
districts = os.path.join(source_files, 'district_bounds')
house_folder = os.path.join(districts,'state_house')
house_shp = gp.read_file(os.path.join(house_folder,'HB 1020 H Red Comm CSBK-25.shp'))
house_shp.head()

DISTRICT                                           geometry
0        1  POLYGON ((850157.570 313952.432, 850174.392 31...
1       10  POLYGON ((700251.524 185408.186, 700232.723 18...
2      109  POLYGON ((402901.840 158912.067, 402916.417 15...
3      110  POLYGON ((416839.438 185947.087, 416909.408 18...
4       83  POLYGON ((453343.349 180266.149, 453459.859 18...

In [54]:
house_shp['DISTRICT'] = house_shp['DISTRICT'].apply(lambda x: x.zfill(3))
house_shp.head()

DISTRICT                                           geometry
0      001  POLYGON ((850157.570 313952.432, 850174.392 31...
1      010  POLYGON ((700251.524 185408.186, 700232.723 18...
2      109  POLYGON ((402901.840 158912.067, 402916.417 15...
3      110  POLYGON ((416839.438 185947.087, 416909.408 18...
4      083  POLYGON ((453343.349 180266.149, 453459.859 18...

In [55]:
sldl_precs_split_list = list(sldl_split_dictionary.keys())
sldl_precs_split = sldl_df[sldl_df['PREC_CO'].isin(sldl_precs_split_list)].copy()
sldl_df_dropped  = sldl_df[~sldl_df['PREC_CO'].isin(sldl_precs_split_list)].copy()
display(sldl_precs_split)
print(len(sldl_precs_split))

PIVOT_COL          PREC_CO  GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  \
264             03-00_WAKE         0.0         0.0         0.0         0.0   
332             04-08_WAKE         0.0         0.0         0.0         0.0   
344             04-16_WAKE         0.0         0.0         0.0         0.0   
346             04-18_WAKE         0.0         0.0         0.0         0.0   
347             04-19_WAKE         0.0         0.0         0.0         0.0   
398             05-07_WAKE         0.0         0.0         0.0         0.0   
451              0601_PITT         0.0         0.0         0.0         0.0   
504             07-10_WAKE         0.0         0.0         0.0         0.0   
547             08-02_WAKE         0.0         0.0         0.0         0.0   
555             08-10_WAKE         0.0         0.0         0.0         0.0   
633               09_WAYNE         0.0         0.0         0.0         0.0   
637             10-02_WAKE         0.0         0.0         0.0         0.0   
649           103_ALAMANCE         0.0         0.0         0.0         0.0   
750         12-13_CABARRUS         0.0         0.0         0.0         0.0   
891             15-01_WAKE         0.0         0.0         0.0         0.0   
892             15-02_WAKE         0.0         0.0         0.0         0.0   
916             1513B_PITT         0.0         0.0         0.0         0.0   
995             18-04_WAKE         0.0         0.0         0.0         0.0   
999             18-08_WAKE         0.0         0.0         0.0         0.0   
1010             18_GASTON         0.0         0.0         0.0         0.0   
1055           20-06A_WAKE         0.0         0.0         0.0         0.0   
1057            20-08_WAKE         0.0         0.0         0.0         0.0   
1096       211_MECKLENBURG         0.0         0.0         0.0         0.0   
1157       241_MECKLENBURG         0.0         0.0         0.0         0.0   
1177         26.1_BUNCOMBE         0.0         0.0         0.0         0.0   
1258           34-2_DURHAM         0.0         0.0         0.0         0.0   
1296             39_GASTON         0.0         0.0         0.0         0.0   
1328         43.2_BUNCOMBE         0.0         0.0         0.0         0.0   
1525       AH49_CUMBERLAND         0.0         0.0         0.0         0.0   
1657       CC31_CUMBERLAND         0.0         0.0         0.0         0.0   
1711          CLEA_SAMPSON         0.0         0.0         0.0         0.0   
1715           CLR4_CRAVEN         0.0         0.0         0.0         0.0   
1739       CU02_CUMBERLAND         0.0         0.0         0.0         0.0   
1953        G8A_CUMBERLAND         0.0         0.0         0.0         0.0   
2067         HU_ROCKINGHAM         0.0         0.0         0.0         0.0   
2074            IH_HAYWOOD         0.0         0.0         0.0         0.0   
2223             N4_CRAVEN         0.0         0.0         0.0         0.0   
2483             P03A_NASH         0.0         0.0         0.0         0.0   
2593         PR04_JOHNSTON         0.0         0.0         0.0         0.0   
2595          PR07_HARNETT         0.0         0.0         0.0         0.0   
2598          PR08_HARNETT         0.0         0.0         0.0         0.0   
2632         PR26_JOHNSTON         0.0         0.0         0.0         0.0   
2747             RBN_MOORE         0.0         0.0         0.0         0.0   
2754             RE_ORANGE         0.0         0.0         0.0         0.0   
2850        SOOX_GRANVILLE         0.0         0.0         4.0         2.0   
3028             WEM_MOORE         0.0         0.0         0.0         0.0   

PIVOT_COL  GSL003DWHI  GSL003RTYS  GSL004DSCH  GSL004RDIX  GSL005DHUN  \
264               0.0         0.0         0.0         0.0         0.0   
332               0.0         0.0         0.0         0.0         0.0   
344               0.0         0.0         0.0         0.0         0.0   
346               0.0         0.0        

46


In [56]:
###ADD DISTRICT COLUMN TO sldl_df_dropped
print(len(sldl_unsplit_dict))
print(len(sldl_df_dropped))
sldl_df_dropped['SLDL_DIST'] = sldl_df_dropped['PREC_CO'].apply(lambda x: sldl_unsplit_dict.get(x))
vest_sub = vest[['PREC_ID','ENR_DESC','COUNTY_NAM','COUNTY_ID','MATCH','geometry']]
sldl_df_dropped = pd.merge(vest_sub,sldl_df_dropped,on='MATCH')
sldl_df_dropped.head()

2616
2616


PREC_ID   ENR_DESC   COUNTY_NAM COUNTY_ID            MATCH  \
0      01  PATTERSON     ALAMANCE         1      01_ALAMANCE   
1      02      COBLE     ALAMANCE         1      02_ALAMANCE   
2      07   ALBRIGHT     ALAMANCE         1      07_ALAMANCE   
3     H08        H08     GUILFORD        41     H08_GUILFORD   
4     079        079  MECKLENBURG        60  079_MECKLENBURG   

                                            geometry          PREC_CO  \
0  POLYGON ((1839239.963 762333.301, 1839240.297 ...      01_ALAMANCE   
1  POLYGON ((1840088.847 807206.254, 1840090.437 ...      02_ALAMANCE   
2  POLYGON ((1871943.040 801230.531, 1871943.510 ...      07_ALAMANCE   
3  POLYGON ((1702354.926 805008.445, 1702627.359 ...     H08_GUILFORD   
4  POLYGON ((1410451.445 548338.307, 1410462.273 ...  079_MECKLENBURG   

   GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  GSL003DWHI  GSL003RTYS  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  GSL006DFUL  GSL006RHAN  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  GSL009DFAR  GSL009RJON  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  GSL011RPOP  GSL012DCOX  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  GSL014RCLE  GSL015DGOM  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  GSL017RILE  GSL018DBUT  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL018RKEN  GSL019DMOR  GSL019RMIL  GSL020DERI  GSL020RDAV  GSL021DSMI  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0  

In [57]:
print(len(sldl_precs_split))
print(len(sldl_split_dictionary))
sldl_precs_split_expanded_list = []
for k,v in sldl_split_dictionary.items():
    sub_dfs = []
    len_splits = len(v)
    for i in range(0,len_splits):
        dist = v[i]
        sub = sldl_precs_split[sldl_precs_split['PREC_CO']==k]
        sub['SLDL_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
        sub['SLDL_DIST'] = sub['SLDL_DIST'].astype(str)
        sub['SLDL_DIST_long'] = sub['SLDL_DIST'].apply(lambda x: ''.join([(' '.join(['[SLDL -',x])),']']))
        sub['UNIQUE_ID'] = sub.apply(lambda x: ' '.join([x['PREC_CO'],x['SLDL_DIST_long']]),axis=1)
        to_keep = []
        for col in sub.columns:
            if col.startswith('GSL'):
                if str(dist) in str(col):
                    to_keep.append(col)
                else:
                    continue
            else:
                to_keep.append(col)
        sub = sub[to_keep]
        sub_dfs.append(sub)
    new_df = pd.concat(sub_dfs)
    sldl_precs_split_expanded_list.append(new_df)
sldl_precs_split_expanded = pd.concat(sldl_precs_split_expanded_list)
sldl_precs_split_expanded = sldl_precs_split_expanded.fillna(0)
sldl_precs_split_expanded_cols = list(sldl_precs_split_expanded.columns)
display(sldl_precs_split_expanded)

46
46


<ipython-input-57-06e5605fdcbf>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['SLDL_DIST'] = sub['PREC_CO'].apply(lambda x: dist)
<ipython-input-57-06e5605fdcbf>:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub['SLDL_DIST'] = sub['SLDL_DIST'].astype(str)
<ipython-input-57-06e5605fdcbf>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata

PIVOT_COL          PREC_CO  GSL041DADC  GSL041LMEI  GSL041RPOP PRECINCT  \
264             03-00_WAKE      2886.0       181.0      2460.0    03-00   
264             03-00_WAKE         0.0         0.0         0.0    03-00   
332             04-08_WAKE         0.0         0.0         0.0    04-08   
332             04-08_WAKE         4.0         0.0         1.0    04-08   
344             04-16_WAKE         0.0         0.0         0.0    04-16   
344             04-16_WAKE         0.0         0.0         0.0    04-16   
346             04-18_WAKE         0.0         0.0         0.0    04-18   
346             04-18_WAKE       456.0        27.0       231.0    04-18   
347             04-19_WAKE         0.0         0.0         0.0    04-19   
347             04-19_WAKE       195.0         9.0       107.0    04-19   
398             05-07_WAKE      1549.0        78.0       618.0    05-07   
398             05-07_WAKE         0.0         0.0         0.0    05-07   
451              0601_PITT         0.0         0.0         0.0     0601   
451              0601_PITT         0.0         0.0         0.0     0601   
504             07-10_WAKE         0.0         0.0         0.0    07-10   
504             07-10_WAKE         0.0         0.0         0.0    07-10   
547             08-02_WAKE         0.0         0.0         0.0    08-02   
547             08-02_WAKE         0.0         0.0         0.0    08-02   
555             08-10_WAKE         0.0         0.0         0.0    08-10   
555             08-10_WAKE         0.0         0.0         0.0    08-10   
633               09_WAYNE         0.0         0.0         0.0       09   
633               09_WAYNE         0.0         0.0         0.0       09   
637             10-02_WAKE         0.0         0.0         0.0    10-02   
637             10-02_WAKE         0.0         0.0         0.0    10-02   
649           103_ALAMANCE         0.0         0.0         0.0      103   
649           103_ALAMANCE         0.0         0.0         0.0      103   
750         12-13_CABARRUS         0.0         0.0         0.0    12-13   
750         12-13_CABARRUS         0.0         0.0         0.0    12-13   
891             15-01_WAKE         0.0         0.0         0.0    15-01   
891             15-01_WAKE         0.0         0.0         0.0    15-01   
892             15-02_WAKE         0.0         0.0         0.0    15-02   
892             15-02_WAKE         0.0         0.0         0.0    15-02   
916             1513B_PITT         0.0         0.0         0.0    1513B   
916             1513B_PITT         0.0         0.0         0.0    1513B   
995             18-04_WAKE         0.0         0.0         0.0    18-04   
995             18-04_WAKE         0.0         0.0         0.0    18-04   
999             18-08_WAKE         0.0         0.0         0.0    18-08   
999             18-08_WAKE         0.0         0.0         0.0    18-08   
1010             18_GASTON         0.0         0.0         0.0       18   
1010             18_GASTON         0.0         0.0         0.0       18   
1055           20-06A_WAKE       723.0        56.0       460.0   20-06A   
1055           20-06A_WAKE         0.0         0.0         0.0   20-06A   
1057            20-08_WAKE       672.0        46.0       392.0    20-08   
1057            20-08_WAKE         0.0         0.0         0.0    20-08   
1096       211_MECKLENBURG         0.0         0.0         0.0      211   
1096       211_MECKLENBURG         0.0         0.0         0.0      211   
1157       241_MECKLENBURG         0.0         0.0         0.0      241   
1157       241_MECKLENBURG         0.0         0.0         0.0      241   
1177         26.1_BUNCOMBE         0.0         0.0         0.0     26.1   
1177         26.1_BUNCOMBE         0.0         0.0         0.0     26.1   
1258           34-2_DURHAM         0.0         0.0         0.0     34-2   
1258           34-2_DURHAM         0.0         0.0         0.0     34-2   
1296             39_GASTO

In [58]:
sldl_dict = make_district_dict(house_shp,'DISTRICT')

In [59]:
new_precs = []
for k,v in sldl_split_dictionary.items():
    original_geom = vest[vest['MATCH']==k]['geometry']
    original_geom = gp.GeoDataFrame(original_geom)
    original_geom_crs = original_geom.crs
    dists = []
    for i in v:
        dist_of_interest = sldl_dict.get(i)
        dists.append(dist_of_interest)
    for i in dists:
        dist_of_interest_geom = i#['geometry']
        district = i['DISTRICT'].unique()[0]
        #print('Current district to split by: ', district)
        dist_of_interest_geom =dist_of_interest_geom.to_crs(original_geom_crs) 
        new_prec = gp.overlay(original_geom, dist_of_interest_geom, how='intersection',keep_geom_type=False)
        new_prec['UNIQUE_ID'] = str(k + ' [SLDL - '+str(district)+ ']')
        new_precs.append(new_prec)
new_precs = pd.concat(new_precs)
display(new_precs)

sldl_precs_split_newgeom = pd.merge(sldl_precs_split_expanded,new_precs,on='UNIQUE_ID',how='outer',indicator=True)
sldl_precs_split_newgeom['SLDL_DIST'] = sldl_precs_split_newgeom['DISTRICT']
sldl_precs_split_newgeom.drop(columns= ['_merge','DISTRICT'],inplace=True)
display(sldl_precs_split_newgeom)

DISTRICT                                           geometry  \
0      041  POLYGON ((2001477.797 677021.200, 2001477.821 ...   
0      037  MULTIPOLYGON (((2037872.555 705980.829, 203787...   
0      049  POLYGON ((2059262.619 752069.877, 2059288.716 ...   
0      041  MULTIPOLYGON (((2057216.886 754536.123, 205722...   
0      036  POLYGON ((2056826.979 729838.275, 2056833.910 ...   
0      011  MULTIPOLYGON (((2060499.995 733932.495, 206050...   
0      049  MULTIPOLYGON (((2064981.242 759745.806, 206498...   
0      041  MULTIPOLYGON (((2064981.171 759777.838, 206498...   
0      036  POLYGON ((2048562.727 740288.889, 2048562.734 ...   
0      041  POLYGON ((2048201.164 738673.378, 2048217.103 ...   
0      041  MULTIPOLYGON (((2050306.932 753511.582, 205028...   
0      040  MULTIPOLYGON (((2042678.518 759836.311, 204267...   
0      012  MULTIPOLYGON (((2524679.929 598378.945, 252467...   
0      009  POLYGON ((2492709.973 644288.415, 2492709.973 ...   
0      049  MULTIPOLYGON (((2080659.413 772951.373, 208078...   
0      040  POLYGON ((2068169.988 776831.755, 2068171.691 ...   
0      049  MULTIPOLYGON (((2088880.119 777085.079, 208886...   
0      040  POLYGON ((2079385.164 782941.394, 2079450.547 ...   
0      049  POLYGON ((2080774.602 773188.294, 2080774.602 ...   
0      040  MULTIPOLYGON (((2080858.851 774333.327, 208085...   
0      021  MULTIPOLYGON (((2296838.162 607590.611, 229683...   
0      010  POLYGON ((2270073.964 595942.516, 2270085.248 ...   
0      039  POLYGON ((2169614.346 767525.362, 2169620.191 ...   
0      035  MULTIPOLYGON (((2174843.475 766754.066, 217484...   
0      064  POLYGON ((1891198.079 835774.599, 1891312.741 ...   
0      063  MULTIPOLYGON (((1893361.508 837478.337, 189336...   
0      083  MULTIPOLYGON (((1529472.857 607408.425, 152965...   
0      082  POLYGON ((1526472.740 610789.857, 1526815.953 ...   
0      037  POLYGON ((2106445.901 669411.423, 2106830.330 ...   
0      033  MULTIPOLYGON (((2127395.532 683599.302, 212739...   
0      036  POLYGON ((2089289.495 697166.853, 2089457.427 ...   
0      033  MULTIPOLYGON (((2099128.452 693669.117, 209933...   
0      012  POLYGON ((2491281.579 644092.444, 2491281.579 ...   
0      009  MULTIPOLYGON (((2498647.748 662572.292, 249864...   
0      036  MULTIPOLYGON (((2094538.128 705645.111, 209453...   
0      011  MULTIPOLYGON (((2079242.370 725928.735, 207927...   
0      036  MULTIPOLYGON (((2070867.417 719561.966, 207089...   
0      011  POLYGON ((2073477.223 726452.860, 2073477.223 ...   
0      108  MULTIPOLYGON (((1373740.465 554134.251, 137374...   
0      109  POLYGON ((1357699.418 548937.093, 1357856.044 ...   
0      041  MULTIPOLYGON (((2033808.618 717929.533, 203380...   
0      037  POLYGON ((2032922.559 716123.883, 2032924.003 ...   
0      041  MULTIPOLYGON (((2037091.183 731875.963, 203711...   
0      037  POLYGON ((2036461.327 728914.609, 2036461.578 ...   
0      107  POLYGON ((1444755.272 592155.269, 1445600.766 ...   
0      101  MULTIPOLYGON (((1449829.254 593517.755, 144987...   
0      098  POLYGON ((1446397.918 608941.083, 1446587.271 ...   
0      107  MULTIPOLYGON (((1474269.818 605252.553, 147426...   
0      116  POLYGON ((920723.504 684912.354, 920754.124 68...   
0      114  MULTIPOLYGON (((928895.614 682447.428, 928895....   
0      029  MULTIPOLYGON (((2022102.117 796518.074, 202211...   
0      031  MULTIPOLYGON (((2028573.028 800544.208, 202861...   
0      108  MULTIPOLYGON (((1367587.247 610045.242, 136910...   
0      110  MULTIPOLYGON (((1348832.762 609703.778, 134884...   
0      116  MULTIPOLYGON (((922449.775 686587.641, 922449....   
0      114  POLYGON ((914836.585 693785.098, 914836.585 69...   
0      045  MULTIPOLYGON (((2008274.956 460981.663, 200834...   
0      044  POLYGON ((1999253.951 463707.852, 1999258.144 ...   
0      045  POLYGON ((2011571.791 464604.285, 2010524.064 ...   
0      044  MULTIPOLYGON (((2011675.965 464621.794, 201157...   
0      021  POLYGON ((2202564.917 473

PREC_CO  GSL041DADC  GSL041LMEI  GSL041RPOP PRECINCT       COUNTY  \
0        03-00_WAKE      2886.0       181.0      2460.0    03-00         WAKE   
1        03-00_WAKE         0.0         0.0         0.0    03-00         WAKE   
2        04-08_WAKE         0.0         0.0         0.0    04-08         WAKE   
3        04-08_WAKE         4.0         0.0         1.0    04-08         WAKE   
4        04-16_WAKE         0.0         0.0         0.0    04-16         WAKE   
5        04-16_WAKE         0.0         0.0         0.0    04-16         WAKE   
6        04-18_WAKE         0.0         0.0         0.0    04-18         WAKE   
7        04-18_WAKE       456.0        27.0       231.0    04-18         WAKE   
8        04-19_WAKE         0.0         0.0         0.0    04-19         WAKE   
9        04-19_WAKE       195.0         9.0       107.0    04-19         WAKE   
10       05-07_WAKE      1549.0        78.0       618.0    05-07         WAKE   
11       05-07_WAKE         0.0         0.0         0.0    05-07         WAKE   
12        0601_PITT         0.0         0.0         0.0     0601         PITT   
13        0601_PITT         0.0         0.0         0.0     0601         PITT   
14       07-10_WAKE         0.0         0.0         0.0    07-10         WAKE   
15       07-10_WAKE         0.0         0.0         0.0    07-10         WAKE   
16       08-02_WAKE         0.0         0.0         0.0    08-02         WAKE   
17       08-02_WAKE         0.0         0.0         0.0    08-02         WAKE   
18       08-10_WAKE         0.0         0.0         0.0    08-10         WAKE   
19       08-10_WAKE         0.0         0.0         0.0    08-10         WAKE   
20         09_WAYNE         0.0         0.0         0.0       09        WAYNE   
21         09_WAYNE         0.0         0.0         0.0       09        WAYNE   
22       10-02_WAKE         0.0         0.0         0.0    10-02         WAKE   
23       10-02_WAKE         0.0         0.0         0.0    10-02         WAKE   
24     103_ALAMANCE         0.0         0.0         0.0      103     ALAMANCE   
25     103_ALAMANCE         0.0         0.0         0.0      103     ALAMANCE   
26   12-13_CABARRUS         0.0         0.0         0.0    12-13     CABARRUS   
27   12-13_CABARRUS         0.0         0.0         0.0    12-13     CABARRUS   
28       15-01_WAKE         0.0         0.0         0.0    15-01         WAKE   
29       15-01_WAKE         0.0         0.0         0.0    15-01         WAKE   
30       15-02_WAKE         0.0         0.0         0.0    15-02         WAKE   
31       15-02_WAKE         0.0         0.0         0.0    15-02         WAKE   
32       1513B_PITT         0.0         0.0         0.0    1513B         PITT   
33       1513B_PITT         0.0         0.0         0.0    1513B         PITT   
34       18-04_WAKE         0.0         0.0         0.0    18-04         WAKE   
35       18-04_WAKE         0.0         0.0         0.0    18-04         WAKE   
36       18-08_WAKE         0.0         0.0         0.0    18-08         WAKE   
37       18-08_WAKE         0.0         0.0         0.0    18-08         WAKE   
38        18_GASTON         0.0         0.0         0.0       18       GASTON   
39        18_GASTON         0.0         0.0         0.0       18       GASTON   
40      20-06A_WAKE       723.0        56.0       460.0   20-06A         WAKE   
41      20-06A_WAKE         0.0         0.0         0.0   20-06A         WAKE   
42       20-08_WAKE       672.0        46.0       392.0    20-08         WAKE   
43       20-08_WAKE         0.0         0.0         0.0    20-08         WAKE   
44  211_MECKLENBURG         0.0         0.0         0.0      211  MECKLENBURG   
45  211_MECKLENBURG         0.0         0.0         0.0      211  MECKLENBURG   
46  241_MECKLENBURG         0.0         0.0         0.0      241  MECKLENBURG   
47  241_MECKLENBURG         0.0         0.0         0.0      241  MECKLENBURG   
48    26.1_BUNCOMBE         0.0         0.0

In [60]:
sldl_precs_split_newgeom = pd.merge(sldl_precs_split_newgeom,vest_sub_split_join,on='MATCH', how = 'outer',indicator = True)
sldl_precs_split_newgeom = sldl_precs_split_newgeom[sldl_precs_split_newgeom['_merge']=='both']
sldl_precs_split_newgeom.drop(columns=['_merge'],inplace=True)
display(sldl_precs_split_newgeom)

PREC_CO  GSL041DADC  GSL041LMEI  GSL041RPOP PRECINCT       COUNTY  \
0        03-00_WAKE      2886.0       181.0      2460.0    03-00         WAKE   
1        03-00_WAKE         0.0         0.0         0.0    03-00         WAKE   
2        04-08_WAKE         0.0         0.0         0.0    04-08         WAKE   
3        04-08_WAKE         4.0         0.0         1.0    04-08         WAKE   
4        04-16_WAKE         0.0         0.0         0.0    04-16         WAKE   
5        04-16_WAKE         0.0         0.0         0.0    04-16         WAKE   
6        04-18_WAKE         0.0         0.0         0.0    04-18         WAKE   
7        04-18_WAKE       456.0        27.0       231.0    04-18         WAKE   
8        04-19_WAKE         0.0         0.0         0.0    04-19         WAKE   
9        04-19_WAKE       195.0         9.0       107.0    04-19         WAKE   
10       05-07_WAKE      1549.0        78.0       618.0    05-07         WAKE   
11       05-07_WAKE         0.0         0.0         0.0    05-07         WAKE   
12        0601_PITT         0.0         0.0         0.0     0601         PITT   
13        0601_PITT         0.0         0.0         0.0     0601         PITT   
14       07-10_WAKE         0.0         0.0         0.0    07-10         WAKE   
15       07-10_WAKE         0.0         0.0         0.0    07-10         WAKE   
16       08-02_WAKE         0.0         0.0         0.0    08-02         WAKE   
17       08-02_WAKE         0.0         0.0         0.0    08-02         WAKE   
18       08-10_WAKE         0.0         0.0         0.0    08-10         WAKE   
19       08-10_WAKE         0.0         0.0         0.0    08-10         WAKE   
20         09_WAYNE         0.0         0.0         0.0       09        WAYNE   
21         09_WAYNE         0.0         0.0         0.0       09        WAYNE   
22       10-02_WAKE         0.0         0.0         0.0    10-02         WAKE   
23       10-02_WAKE         0.0         0.0         0.0    10-02         WAKE   
24     103_ALAMANCE         0.0         0.0         0.0      103     ALAMANCE   
25     103_ALAMANCE         0.0         0.0         0.0      103     ALAMANCE   
26   12-13_CABARRUS         0.0         0.0         0.0    12-13     CABARRUS   
27   12-13_CABARRUS         0.0         0.0         0.0    12-13     CABARRUS   
28       15-01_WAKE         0.0         0.0         0.0    15-01         WAKE   
29       15-01_WAKE         0.0         0.0         0.0    15-01         WAKE   
30       15-02_WAKE         0.0         0.0         0.0    15-02         WAKE   
31       15-02_WAKE         0.0         0.0         0.0    15-02         WAKE   
32       1513B_PITT         0.0         0.0         0.0    1513B         PITT   
33       1513B_PITT         0.0         0.0         0.0    1513B         PITT   
34       18-04_WAKE         0.0         0.0         0.0    18-04         WAKE   
35       18-04_WAKE         0.0         0.0         0.0    18-04         WAKE   
36       18-08_WAKE         0.0         0.0         0.0    18-08         WAKE   
37       18-08_WAKE         0.0         0.0         0.0    18-08         WAKE   
38        18_GASTON         0.0         0.0         0.0       18       GASTON   
39        18_GASTON         0.0         0.0         0.0       18       GASTON   
40      20-06A_WAKE       723.0        56.0       460.0   20-06A         WAKE   
41      20-06A_WAKE         0.0         0.0         0.0   20-06A         WAKE   
42       20-08_WAKE       672.0        46.0       392.0    20-08         WAKE   
43       20-08_WAKE         0.0         0.0         0.0    20-08         WAKE   
44  211_MECKLENBURG         0.0         0.0         0.0      211  MECKLENBURG   
45  211_MECKLENBURG         0.0         0.0         0.0      211  MECKLENBURG   
46  241_MECKLENBURG         0.0         0.0         0.0      241  MECKLENBURG   
47  241_MECKLENBURG         0.0         0.0         0.0      241  MECKLENBURG   
48    26.1_BUNCOMBE         0.0         0.0

In [61]:
##CONCAT THE DFS
sldl_final_df = pd.concat([sldl_df_dropped,sldl_precs_split_newgeom])
sldl_final_df['UNIQUE_ID'] = sldl_final_df['UNIQUE_ID'].astype(str)
sldl_final_df = sldl_final_df.fillna(0)
display(sldl_final_df.head())
display(sldl_final_df.tail())

PREC_ID   ENR_DESC   COUNTY_NAM COUNTY_ID            MATCH  \
0      01  PATTERSON     ALAMANCE         1      01_ALAMANCE   
1      02      COBLE     ALAMANCE         1      02_ALAMANCE   
2      07   ALBRIGHT     ALAMANCE         1      07_ALAMANCE   
3     H08        H08     GUILFORD        41     H08_GUILFORD   
4     079        079  MECKLENBURG        60  079_MECKLENBURG   

                                            geometry          PREC_CO  \
0  POLYGON ((1839239.963 762333.301, 1839240.297 ...      01_ALAMANCE   
1  POLYGON ((1840088.847 807206.254, 1840090.437 ...      02_ALAMANCE   
2  POLYGON ((1871943.040 801230.531, 1871943.510 ...      07_ALAMANCE   
3  POLYGON ((1702354.926 805008.445, 1702627.359 ...     H08_GUILFORD   
4  POLYGON ((1410451.445 548338.307, 1410462.273 ...  079_MECKLENBURG   

   GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  GSL003DWHI  GSL003RTYS  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  GSL006DFUL  GSL006RHAN  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  GSL009DFAR  GSL009RJON  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  GSL011RPOP  GSL012DCOX  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  GSL014RCLE  GSL015DGOM  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  GSL017RILE  GSL018DBUT  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL018RKEN  GSL019DMOR  GSL019RMIL  GSL020DERI  GSL020RDAV  GSL021DSMI  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0  

PREC_ID                ENR_DESC COUNTY_NAM COUNTY_ID           MATCH  \
87      RE           ROGER EUBANKS     ORANGE        68       RE_ORANGE   
88    SOOX  Voting District 00SOOX  GRANVILLE        39  SOOX_GRANVILLE   
89    SOOX  Voting District 00SOOX  GRANVILLE        39  SOOX_GRANVILLE   
90     WEM               WESTMOORE      MOORE        63       WEM_MOORE   
91     WEM               WESTMOORE      MOORE        63       WEM_MOORE   

                                             geometry         PREC_CO  \
87  POLYGON ((1977488.971 811449.266, 1977535.707 ...       RE_ORANGE   
88  MULTIPOLYGON (((2125224.839 925466.433, 212523...  SOOX_GRANVILLE   
89  POLYGON ((2125934.540 926085.490, 2125957.737 ...  SOOX_GRANVILLE   
90  POLYGON ((1780716.803 642104.498, 1784412.286 ...       WEM_MOORE   
91  MULTIPOLYGON (((1784419.271 642154.923, 178457...       WEM_MOORE   

    GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  GSL003DWHI  GSL003RTYS  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         4.0         2.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  GSL006DFUL  GSL006RHAN  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  GSL009DFAR  GSL009RJON  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  GSL011RPOP  GSL012DCOX  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  GSL014RCLE  GSL015DGOM  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  GSL017RILE  GSL018DBUT  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL018RKEN  GSL019DMOR  GSL019RMIL  GSL020DERI  GSL020RDAV  GSL021DSMI  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0   

In [62]:
sldl_final_df['COUNTY_ID'] = sldl_final_df['COUNTY_ID'].astype(str)
sldl_final_df['COUNTYFP'] = sldl_final_df['COUNTY_ID'].apply(lambda x: str(x).zfill(3))
sldl_final_df['UNIQUE_ID'] = sldl_final_df.apply(lambda x: x['MATCH'] if x['UNIQUE_ID']=='nan' else x['UNIQUE_ID'],axis=1)
sldl_final_df.drop(columns = ['PREC_CO','MATCH','PRECINCT','COUNTY','SLDL_DIST_long'],inplace=True)
sldl_final_df_cols = list(sldl_final_df.columns)
sldl_final_df_cols.remove('geometry')
sldl_final_df_cols.remove('SLDL_DIST')
sldl_final_df_cols.remove('UNIQUE_ID')
sldl_final_df_cols.remove('COUNTYFP')
sldl_final_df_cols[0:1] = ['UNIQUE_ID','COUNTYFP']
sldl_final_df_cols[5:5] = ['SLDL_DIST']
sldl_final_df_cols.append('geometry')
sldl_final_df = sldl_final_df[sldl_final_df_cols]
display(sldl_final_df.head())
display(sldl_final_df.tail())

UNIQUE_ID COUNTYFP   ENR_DESC   COUNTY_NAM COUNTY_ID SLDL_DIST  \
0      01_ALAMANCE      001  PATTERSON     ALAMANCE         1       064   
1      02_ALAMANCE      001      COBLE     ALAMANCE         1       064   
2      07_ALAMANCE      001   ALBRIGHT     ALAMANCE         1       064   
3     H08_GUILFORD      041        H08     GUILFORD        41       060   
4  079_MECKLENBURG      060        079  MECKLENBURG        60       101   

   GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  GSL003DWHI  GSL003RTYS  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  GSL006DFUL  GSL006RHAN  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  GSL009DFAR  GSL009RJON  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  GSL011RPOP  GSL012DCOX  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  GSL014RCLE  GSL015DGOM  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  GSL017RILE  GSL018DBUT  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL018RKEN  GSL019DMOR  GSL019RMIL  GSL020DERI  GSL020RDAV  GSL021DSMI  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   GSL021RHEA  GSL022DKIR  GSL022RBRI  GSL023DWIL  GSL023GLAN  GSL023RHOL  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3        

UNIQUE_ID COUNTYFP                ENR_DESC COUNTY_NAM  \
87       RE_ORANGE [SLDL - 050]      068           ROGER EUBANKS     ORANGE   
88  SOOX_GRANVILLE [SLDL - 002]      039  Voting District 00SOOX  GRANVILLE   
89  SOOX_GRANVILLE [SLDL - 032]      039  Voting District 00SOOX  GRANVILLE   
90       WEM_MOORE [SLDL - 052]      063               WESTMOORE      MOORE   
91       WEM_MOORE [SLDL - 078]      063               WESTMOORE      MOORE   

   COUNTY_ID SLDL_DIST  GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  \
87        68       050         0.0         0.0         0.0         0.0   
88        39       002         0.0         0.0         4.0         2.0   
89        39       032         0.0         0.0         0.0         0.0   
90        63       052         0.0         0.0         0.0         0.0   
91        63       078         0.0         0.0         0.0         0.0   

    GSL003DWHI  GSL003RTYS  GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL006DFUL  GSL006RHAN  GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL009DFAR  GSL009RJON  GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL011RPOP  GSL012DCOX  GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL014RCLE  GSL015DGOM  GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL017RILE  GSL018DBUT  GSL018RKEN  GSL019DMOR  GSL019RMIL  GSL020DERI  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0         0.0         0.0   
90         0.0         0.0         0.0         0.0         0.0         0.0   
91         0.0         0.0         0.0         0.0         0.0         0.0   

    GSL020RDAV  GSL021DSMI  GSL021RHEA  GSL022DKIR  GSL022RBRI  GSL023DWIL  \
87         0.0         0.0         0.0         0.0         0.0         0.0   
88         0.0         0.0         0.0         0.0         0.0         0.0   
89         0.0         0.0         0.0         0.0    

In [63]:
sldl_final_df = sldl_final_df.fillna(0)
for i in sldl_final_df.columns:
    if i.startswith('G'):
        sldl_final_df[i] = sldl_final_df[i].astype(int)
    elif i!='geometry':
        sldl_final_df[i] = sldl_final_df[i].astype(str)
    else:
        continue
display(sldl_final_df)

UNIQUE_ID COUNTYFP                ENR_DESC   COUNTY_NAM  \
0                   01_ALAMANCE      001               PATTERSON     ALAMANCE   
1                   02_ALAMANCE      001                   COBLE     ALAMANCE   
2                   07_ALAMANCE      001                ALBRIGHT     ALAMANCE   
3                  H08_GUILFORD      041                     H08     GUILFORD   
4               079_MECKLENBURG      060                     079  MECKLENBURG   
..                          ...      ...                     ...          ...   
87       RE_ORANGE [SLDL - 050]      068           ROGER EUBANKS       ORANGE   
88  SOOX_GRANVILLE [SLDL - 002]      039  Voting District 00SOOX    GRANVILLE   
89  SOOX_GRANVILLE [SLDL - 032]      039  Voting District 00SOOX    GRANVILLE   
90       WEM_MOORE [SLDL - 052]      063               WESTMOORE        MOORE   
91       WEM_MOORE [SLDL - 078]      063               WESTMOORE        MOORE   

   COUNTY_ID SLDL_DIST  GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  \
0          1       064           0           0           0           0   
1          1       064           0           0           0           0   
2          1       064           0           0           0           0   
3         41       060           0           0           0           0   
4         60       101           0           0           0           0   
..       ...       ...         ...         ...         ...         ...   
87        68       050           0           0           0           0   
88        39       002           0           0           4           2   
89        39       032           0           0           0           0   
90        63       052           0           0           0           0   
91        63       078           0           0           0           0   

    GSL003DWHI  GSL003RTYS  GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  \
0            0           0           0           0           0           0   
1            0           0           0           0           0           0   
2            0           0           0           0           0           0   
3            0           0           0           0           0           0   
4            0           0           0           0           0           0   
..         ...         ...         ...         ...         ...         ...   
87           0           0           0           0           0           0   
88           0           0           0           0           0           0   
89           0           0           0           0           0           0   
90           0           0           0           0           0           0   
91           0           0           0           0           0           0   

    GSL006DFUL  GSL006RHAN  GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  \
0            0           0           0           0           0           0   
1            0           0           0           0           0           0   
2            0           0           0           0           0           0   
3            0           0           0           0           0           0   
4            0           0           0           0           0           0   
..         ...         ...         ...         ...         ...         ...   
87           0           0           0           0           0           0   
88           0           0           0           0           0           0   
89           0           0           0           0           0           0   
90           0           0           0           0           0           0   
91           0           0           0           0           0           0   

    GSL009DFAR  GSL009RJON  GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  \
0            0           0           0           0           0           0   
1            0           0           0           0           0           0   
2            0           0           0           0  

In [64]:
sldl_final_df.head()

UNIQUE_ID COUNTYFP   ENR_DESC   COUNTY_NAM COUNTY_ID SLDL_DIST  \
0      01_ALAMANCE      001  PATTERSON     ALAMANCE         1       064   
1      02_ALAMANCE      001      COBLE     ALAMANCE         1       064   
2      07_ALAMANCE      001   ALBRIGHT     ALAMANCE         1       064   
3     H08_GUILFORD      041        H08     GUILFORD        41       060   
4  079_MECKLENBURG      060        079  MECKLENBURG        60       101   

   GSL001DNIC  GSL001RGOO  GSL002DDEP  GSL002RYAR  GSL003DWHI  GSL003RTYS  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL004DSCH  GSL004RDIX  GSL005DHUN  GSL005RKIR  GSL006DFUL  GSL006RHAN  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL007DSTO  GSL007RWIN  GSL008DSMI  GSL008RMOO  GSL009DFAR  GSL009RJON  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL010DMAR  GSL010RBEL  GSL011DDAH  GSL011LTRA  GSL011RPOP  GSL012DCOX  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL012RHUM  GSL013DBAY  GSL013RMCE  GSL014DWOF  GSL014RCLE  GSL015DGOM  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL015RSHE  GSL016DFIN  GSL016RSMI  GSL017DSIM  GSL017RILE  GSL018DBUT  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL018RKEN  GSL019DMOR  GSL019RMIL  GSL020DERI  GSL020RDAV  GSL021DSMI  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   GSL021RHEA  GSL022DKIR  GSL022RBRI  GSL023DWIL  GSL023GLAN  GSL023RHOL  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3        

In [65]:
sldl_final_df.to_file('./nc_gen_20_sldl_prec.shp')

### Validate election totals

In [66]:
list_of_dfs = [sldu_vest_df,cong_final_df,sldl_final_df]
df_names = ['SLDU','CONG','SLDL']
data_dict = dict(zip(df_names,list_of_dfs))

totals_dict = {}
for df_name,df in data_dict.items():
    col_tots = []
    col_names = []
    for col in df.columns:
        if col.startswith('G'):
            col_tots.append(int(df[col].sum()))
            col_names.append(col)
    df_dict = dict(zip(col_names,col_tots))
    totals_dict.update({df_name:df_dict})

In [67]:
race_cols = []
race_totals = []
for k,v in totals_dict.items():
    print('***',k,'***')
    for i,j in v.items():
        print(i, '\t', j)
        race_cols.append(i)
        race_totals.append(j)
    print('')
export_dict = {'CANDIDATE':race_cols,'RDH TOTAL': race_totals}
export_dict_df = pd.DataFrame.from_dict(export_dict)
display(export_dict_df.head())

*** SLDU ***
G20PRERTRU 	 2758775
G20PREDBID 	 2684292
G20PRELJOR 	 48678
G20PREGHAW 	 12195
G20PRECBLA 	 7549
G20PREOWRI 	 13315
G20USSRTIL 	 2665598
G20USSDCUN 	 2569965
G20USSLBRA 	 171571
G20USSCHAY 	 67818
G20GOVRFOR 	 2586605
G20GOVDCOO 	 2834790
G20GOVLDIF 	 60449
G20GOVCPIS 	 20934
G20LTGRROB 	 2800656
G20LTGDHOL 	 2623458
G20ATGRONE 	 2699778
G20ATGDSTE 	 2713400
G20TRERFOL 	 2812799
G20TREDCHA 	 2537019
G20SOSRSYK 	 2630559
G20SOSDMAR 	 2755571
G20AUDRSTR 	 2635825
G20AUDDWOO 	 2730175
G20AGRRTRO 	 2901849
G20AGRDWAD 	 2485722
G20INSRCAU 	 2775488
G20INSDGOO 	 2586464
G20LABRDOB 	 2726619
G20LABDHOL 	 2637528
G20SPIRTRU 	 2753220
G20SPIDMAN 	 2605169
G20SSCRNEW 	 2695951
G20SSCDBEA 	 2695550
G20SSCRBER 	 2723704
G20SSCDINM 	 2652187
G20SSCRBAR 	 2746362
G20SSCDDAV 	 2616265
G20SACRWOO 	 2767469
G20SACDSHI 	 2577013
G20SACRGOR 	 2735952
G20SACDCUB 	 2600632
G20SACRDIL 	 2769020
G20SACDSTY 	 2561090
G20SACRCAR 	 2747109
G20SACDYOU 	 2578035
G20SACRGRI 	 2720503
G20SACDBRO 	 259

CANDIDATE  RDH TOTAL
0  G20PRERTRU    2758775
1  G20PREDBID    2684292
2  G20PRELJOR      48678
3  G20PREGHAW      12195
4  G20PRECBLA       7549

In [68]:
export_dict_df.to_csv('./verify_totals.csv')

In [69]:
non_value_columns = ['UNIQUE_ID','COUNTYFP','ENR_DESC','COUNTY_NAM','COUNTY_ID','SLDL_DIST','CONG_DIST','geometry']
for index,row in sldl_final_df.iterrows():
    for val in row.index:
        district_assignment = row['SLDL_DIST']
#non_value_columns is a list of the columns that don't contain races
        if val not in non_value_columns and row[val] != 0:
            # In the below [4:6] is where the district assignment is in the string
            if (val[3:6] != district_assignment):
                print("District Assignment: ", district_assignment)
                print("Value" , val[4:6])
                print("Column", val)
                print(row["UNIQUE_ID"])
                print(" ")

In [70]:
non_value_columns = ['UNIQUE_ID','COUNTYFP','ENR_DESC','COUNTY_NAM','COUNTY_ID','CONG_DIST','geometry']
for index,row in cong_final_df.iterrows():
    for val in row.index:
        district_assignment = row['CONG_DIST']
#non_value_columns is a list of the columns that don't contain races
        if val not in non_value_columns and row[val] != 0:
            # In the below [4:6] is where the district assignment is in the string
            if (val[4:6] != district_assignment):
                print("District Assignment: ", district_assignment)
                print("Value" , val[4:6])
                print("Column", val)
                print(row["UNIQUE_ID"])
                print(" ")